In [4]:
#Converted to Method...

import collections as coll
import math
import pickle
import string

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import numpy as np
from matplotlib import style
from nltk.corpus import cmudict
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize, sent_tokenize
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler

import nltk

nltk.download('cmudict')
nltk.download('stopwords')

style.use("ggplot")
cmuDictionary = None


[nltk_data] Downloading package cmudict to
[nltk_data]     /Users/kimkwangil/nltk_data...
[nltk_data]   Package cmudict is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/kimkwangil/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [11]:


# 텍스트 한 단락을 취해서 그것을 지정된 수의 문장으로 나눈다.
def slidingWindow(sequence, winSize, step=1):
    try:
        it = iter(sequence)
        print ('slideingWinows it :', it)
        #slideingWinows it : <str_iterator object at 0x7fe51178b910>  #작동할 때 결과
    except TypeError:
        raise Exception("**ERROR** sequence must be iterable.")
    if not ((type(winSize) == type(0)) and (type(step) == type(0))):
        raise Exception("**ERROR** type(winSize) and type(step) must be int.")
    if step > winSize:
        raise Exception("**ERROR** step must not be larger than winSize.")
    if winSize > len(sequence):
        raise Exception("**ERROR** winSize must not be larger than sequence length.")

    sequence = sent_tokenize(sequence)

    # 생략할 사전 계산 청크 수
    numOfChunks = int(((len(sequence) - winSize) / step) + 1)

    l = []
    for i in range(0, numOfChunks * step, step):
        l.append(" ".join(sequence[i:i + winSize]))

    return l



#모음수 세기
def syllable_count_Manual(word):
    word = word.lower()
    count = 0
    vowels = "aeiouy"
    if word[0] in vowels:
        count += 1
    for index in range(1, len(word)):
        if word[index] in vowels and word[index - 1] not in vowels:
            count += 1
            if word.endswith("e"):
                count -= 1
    if count == 0:
        count += 1
    print("vowels numbers:", count)
    return count



# COUNTS NUMBER OF 음절을 소문자로 바꾸고 문자열만 가져와서 에세이 내에서 음절이 몇개인지 카운트
def syllable_count(word):
    global cmuDictionary #사전을 사용하여 syl 수를 세어서 가저옴
    d = cmuDictionary
    try:
        syl = [len(list(y for y in x if y[-1].isdigit())) for x in d[word.lower()]][0]
    except:
        syl = syllable_count_Manual(word)
    # print("syllable numbers:", syl)
    return syl




# removing stop words, 구두점 등의 문장기호 제거하고 단어 평균 길이 계사
def Avg_wordLength(str):
    str.translate(string.punctuation)
    tokens = word_tokenize(str, language='english')
    st = [",", ".", "'", "!", '"', "#", "$", "%", "&", "(", ")", "*", "+", "-", ".", "/", ":", ";", "<", "=", '>', "?",
          "@", "[", "\\", "]", "^", "_", '`', "{", "|", "}", '~', '\t', '\n', 'u00e9', '[', ']', 'n','n201', '\u201d' ]
    stop = stopwords.words('english') + st
    words = [word for word in tokens if word not in stop]
    return np.average([len(word) for word in words])




# 문장수 계산
def Avg_SentLenghtByCh(text):
    tokens = sent_tokenize(text)
    return np.average([len(token) for token in tokens])




# 문장의 평균 단어 수 반환
def Avg_SentLenghtByWord(text):
    tokens = sent_tokenize(text)
    return np.average([len(token.split()) for token in tokens])



# 불용어 제거하고 단어당 음절 수를 파악하여 가독성 계산에 반영
def Avg_Syllable_per_Word(text):
    tokens = word_tokenize(text, language='english')
    st = [",", ".", "'", "!", '"', "#", "$", "%", "&", "(", ")", "*", "+", "-", ".", "/", ":", ";", "<", "=", '>', "?",
          "@", "[", "\\", "]", "^", "_", '`', "{", "|", "}", '~', '\t', '\n']
    stop = stopwords.words('english') + st
    words = [word for word in tokens if word not in stop]
    syllabls = [syllable_count(word) for word in words]
    p = (" ".join(words))
    return sum(syllabls) / max(1, len(words))




# 청크 길이에서 정규화된 특수 문자 수
def CountSpecialCharacter(text):
    st = ["#", "$", "%", "&", "(", ")", "*", "+", "-", "/", "<", "=", '>',
          "@", "[", "\\", "]", "^", "_", '`', "{", "|", "}", '~', '\t', '\n']
    count = 0
    for i in text:
        if (i in st):
            count = count + 1
    return count / len(text)




def CountPuncuation(text):
    st = [",", ".", "'", "!", '"', ";", "?", ":", ";"]
    count = 0
    for i in text:
        if (i in st):
            count = count + 1
    return float(count) / float(len(text))



# 기능어 수를 파악, 물론 특수문자 제거
# 온라인 메시지 작성자 식별: 쓰기 유형 특성 및 분류 기법을 용

def CountFunctionalWords(text):
    functional_words = """a between in nor some upon
    about both including nothing somebody us
    above but inside of someone used
    after by into off something via
    all can is on such we
    although cos it once than what
    am do its one that whatever
    among down latter onto the when
    an each less opposite their where
    and either like or them whether
    another enough little our these which
    any every lots outside they while
    anybody everybody many over this who
    anyone everyone me own those whoever
    anything everything more past though whom
    are few most per through whose
    around following much plenty till will
    as for must plus to with
    at from my regarding toward within
    be have near same towards without
    because he need several under worth
    before her neither she unless would
    behind him no should unlike yes
    below i nobody since until you
    beside if none so up your
    """

    functional_words = functional_words.split()
    words = RemoveSpecialCHs(text)
    count = 0

    for i in text:
        if i in functional_words:
            count += 1

    return count / len(words)




# 표현다양성 파악하기 위해 추출해야 값
def hapaxLegemena(text):
    words = RemoveSpecialCHs(text)
    V1 = 0
    # dictionary comprehension . har word kay against value 0 kardi
    freqs = {key: 0 for key in words}
    for word in words: # 단어중 유일한 단어들이 몇개인가 세어서 
        freqs[word] += 1
    for word in freqs:
        if freqs[word] == 1:
            V1 += 1
    N = len(words)
    V = float(len(set(words)))
    R = 100 * math.log(N) / max(1, (1 - (V1 / V))) # 독특한 단어의 비율을 확률로 계산
    h = V1 / N
    return R, h




#동일한 단어가 얼마나 사용되는지 파악
def hapaxDisLegemena(text):
    words = RemoveSpecialCHs(text)
    count = 0

    freqs = coll.Counter()
    freqs.update(words)
    for word in freqs:
        if freqs[word] == 2:
            count += 1

    h = count / float(len(words))
    S = count / float(len(set(words)))
    return S, h




#어휘 풍부성 파악
def AvgWordFrequencyClass(text):
    words = RemoveSpecialCHs(text)
    # dictionary comprehension . har word kay against value 0 kardi
    freqs = {key: 0 for key in words}
    for word in words:
        freqs[word] += 1
    maximum = float(max(list(freqs.values())))
    return np.average([math.floor(math.log((maximum + 1) / (freqs[word]) + 1, 2)) for word in words])




# 총 단어를 토큰화하여 중복되지 않는 토큰의 비율 계산
def typeTokenRatio(text):
    words = word_tokenize(text)
    return len(set(words)) / len(words)




# logW = V-a/log(N)
# N = total words , V = vocabulary richness (unique words) ,  a=0.17
# 문장내 다른 단어들을 파악하기 위해서 설정
def BrunetsMeasureW(text):
    words = RemoveSpecialCHs(text)
    a = 0.17
    V = float(len(set(words)))
    N = len(words)
    B = (V - a) / (math.log(N))
    return B




def RemoveSpecialCHs(text):
    text = word_tokenize(text)
    st = [",", ".", "'", "!", '"', "#", "$", "%", "&", "(", ")", "*", "+", "-", ".", "/", ":", ";", "<", "=", '>', "?",
          "@", "[", "\\", "]", "^", "_", '`', "{", "|", "}", '~', '\t', '\n']

    words = [word for word in text if word not in st]
    return words




# K  10,000 * (M - N) / N**2
# , where M  Sigma i**2 * Vi.
def YulesCharacteristicK(text):
    words = RemoveSpecialCHs(text)
    N = len(words)
    freqs = coll.Counter()
    freqs.update(words)
    vi = coll.Counter()
    vi.update(freqs.values())
    M = sum([(value * value) * vi[value] for key, value in freqs.items()])
    K = 10000 * (M - N) / math.pow(N, 2)
    return K




# -1*sigma(pi*lnpi)
# Shannon과 Simpsons 다양성 지수 활용
def ShannonEntropy(text):
    words = RemoveSpecialCHs(text)
    lenght = len(words)
    freqs = coll.Counter()
    freqs.update(words)
    arr = np.array(list(freqs.values()))
    distribution = 1. * arr
    distribution /= max(1, lenght)
    import scipy as sc
    H = sc.stats.entropy(distribution, base=2)
    # H = sum([(i/lenght)*math.log(i/lenght,math.e) for i in freqs.values()])
    return H




# 1 - (sigma(n(n - 1))/N(N-1)
# N is total number of words
# n is the number of each type of word
def SimpsonsIndex(text):
    words = RemoveSpecialCHs(text)
    freqs = coll.Counter()
    freqs.update(words)
    N = len(words)
    n = sum([1.0 * i * (i - 1) for i in freqs.values()])
    D = 1 - (n / (N * (N - 1)))
    return D




def FleschReadingEase(text, NoOfsentences):
    words = RemoveSpecialCHs(text)
    l = float(len(words))
    scount = 0
    for word in words:
        scount += syllable_count(word)

    I = 206.835 - 1.015 * (l / float(NoOfsentences)) - 84.6 * (scount / float(l))
    return I




def FleschCincadeGradeLevel(text, NoOfSentences):
    words = RemoveSpecialCHs(text)
    scount = 0
    for word in words:
        scount += syllable_count(word)

    l = len(words)
    F = 0.39 * (l / NoOfSentences) + 11.8 * (scount / float(l)) - 15.59
    return F



def dale_chall_readability_formula(text, NoOfSectences):
    words = RemoveSpecialCHs(text)
    difficult = 0
    adjusted = 0
    NoOfWords = len(words)
    #with open('J:\Django\EssayFit_Django\essayfitaiproject\essayai\data\dale-chall.pkl', 'rb') as f:
    #with open('/Users/jongphilkim/Desktop/Django_WEB/01_ESSAYFITAI_11-02/essayfitaiproject/essayai/data/dale-chall.pkl', 'rb') as f:
    with open('dale-chall.pkl', 'rb') as f:
        fimiliarWords = pickle.load(f)
    for word in words:
        if word not in fimiliarWords:
            difficult += 1
    percent = (difficult / NoOfWords) * 100
    if (percent > 5):
        adjusted = 3.6365
    D = 0.1579 * (percent) + 0.0496 * (NoOfWords / NoOfSectences) + adjusted
    return D



def GunningFoxIndex(text, NoOfSentences):
    words = RemoveSpecialCHs(text)
    NoOFWords = float(len(words))
    complexWords = 0
    for word in words:
        if (syllable_count(word) > 2):
            complexWords += 1

    G = 0.4 * ((NoOFWords / NoOfSentences) + 100 * (complexWords / NoOFWords))
    return G


def PrepareData(text1, text2, Winsize):
    chunks1 = slidingWindow(text1, Winsize, Winsize)
    chunks2 = slidingWindow(text2, Winsize, Winsize)
    return " ".join(str(chunk1) + str(chunk2) for chunk1, chunk2 in zip(chunks1, chunks2))


In [12]:
def FeatureExtration(text, winSize, step):
    # cmu dictionary for syllables
    global cmuDictionary
    cmuDictionary = cmudict.dict()

    chunks = slidingWindow(text, winSize, step)

    vector = []

    for chunk in chunks:

        feature = []

        # VOCABULARY 풍부성 특징들 파악
        # 총 단어를 토큰화하여 중복되지 않는 토큰의 비율 계산
        TTratio = round(typeTokenRatio(chunk), 2)
        feature.append(TTratio)
        print("TTratio 표현다양성: ", TTratio)
        # token_ratio.append(TTratio)

        # 표현다양성 파악(전체 단어에서 유일한 단어 사용비율)
        HonoreMeasureR, hapax = hapaxLegemena(chunk)
        feature.append(HonoreMeasureR)
        print('HonoreMeasureR 표현다양성 :', HonoreMeasureR)
        feature.append(hapax)
        print('hapax 표현다양성 :', hapax )


        #다양성 지수 분석
        YuleK = round(YulesCharacteristicK(chunk),2)
        feature.append(YuleK)
        print('YuleK 다양성지수:',YuleK )
        # YuleK__.append(YuleK)

        # Shannon과 Simpsons 다양성 지수 활용
        S = round(SimpsonsIndex(chunk), 2)
        feature.append(S)
        print('SimpsonIndex 다양성지수', S)
        # S__.append(S)

        Shannon = round(ShannonEntropy(text),2)
        feature.append(Shannon)
        # Shannon__.append(Shannon)
        print('Shannon 다양성지수:', Shannon)

        # 가독성
        FR = round(FleschReadingEase(chunk, winSize),2)
        feature.append(FR)
        print("FR_readerablity :", FR)

        vector.append(feature)

    return vector




text_input = """A window into the soul.For most people, this would be the eyes. The eyes cannot lie; they often tell more about a person's emotions than their words. What distinguishes a fake smile from a genuine one? The eyes. What shows sadness? The eyes. What gives away a liar? The eyes.But are the eyes the only window into the soul?Recently, I began painting with watercolors. With watercolors, there is no turning back: if one section is too dark, it is nearly impossible to lighten the area again. Every stroke must be done purposefully, every color mixed to its exact value.I laid my materials before me, preparing myself for the worst. I checked my list of supplies, making sure my setup was perfect.I wet my brush, dipped it into some yellow ochre, and dabbed off the excess paint. Too little water on my brush. I dipped my brush back into my trusty water jar; the colors swirled beautifully, forming an abstract art piece before my eyes. \u2014It's a shame that I couldn't appreciate it.I continued mixing colors to their exact value. More alizarin crimson. More water. More yellow ochre. Less water. More phthalo blue. The cycle continued. Eventually, I was satisfied. The colors looked good, there was enough contrast between facial features, and the watercolors stayed inside the lines.Craving feedback, I posted my art to Snapchat. I got a few messages such as 'wow' and 'pretty,' but one message stood out. 'You were anxious with this one, huh? Anyways, love the hair!'I was caught off guard. Was it a lucky guess? Did they know something I didn't? I immediately responded: 'Haha, how could you tell?' No response.What I didn't know at the time was that my response would come a few months later while babysitting. Since the girl I was babysitting loved art, I took out some Crayola watercolors and some watercolor paper for her to play with. After I went to the bathroom and came back, the watercolors were doused with water. 'You were impatient with this one, huh? Anyways, love the little dog you drew!'The little girl looked up at me, confused. 'How could you tell?' 'You used a lot of water for a brighter color, but you couldn't wait for it to slowly soak in.''Oh.'Now, I would be lying if I said I realized the connection between the two events immediately.Instead, I made the connection when I decided to sit down one day and objectively critique my art. The piece that I once loved now seemed like a nervous wreck: the paper was overworked, the brushstrokes were undecided, the facial features blended together, and each drop of water was bound inside the lines as if it was a prisoner in a cage.From then on, I started noticing pieces of personality in additional creations surrounding me: website designs, solutions to math problems, code written for class, and even the preparation of a meal.When I peer around at people's projects during Code Club, I notice the clear differences between their code. Some people break it up by commenting in every possible section. Others breeze through the project, not caring to comment or organize their code. I could also see clear differences in personalities when our club members began coding the Arduino for the first time. Some followed the tutorials to the letter, while others immediately started experimenting with different colored LEDs and ways of wiring the circuit.It became clear to me that, as humans, we leave pieces of our souls in everything we do, more than we intend to. If we entertain this thought, perhaps the key to better understanding others around us is simply noticing the subtler clues under our noses?Perhaps there are endless windows to the soul, and we simply need to peer through them. I shakily rose my hand. 'We should create workshops of our own,' I suggested.I got a few strange looks. 'It's a good idea, but it's too much work.' 'We just don't have enough free time to make it work.' 'Maybe we could, but I don't know how to make workshops.' My suggestion was shot down. I shuffled in my seat. 'I could make them.' A few people stared at me in disbelief. I glanced over at the club advisor, Mr. C, nervous to hear his response.'If you're willing to take on the work, we can try it.' Mr. C replied. And so I embarked on my quest. I researched different workshops on the internet, learning the information myself at first. Then, I transitioned into creating workshops of my own, making sure that the information was easy to understand for even a beginner. I was exhausted; my first workshop took 16 cumulative hours to create."""


In [13]:
#!/usr/bin/python
# -*- coding:utf-8 -*-

import json
import pandas as pd
import sys
import os

In [14]:
pwd

'/Users/kimkwangil/Documents/008_AI/Story_Analysis-master 13/ai_writing_analysis'

In [15]:
path = "/Users/kimkwangil/Documents/008_AI/Story_Analysis-master 8/01_THEME_/ps_data/"
file_list = os.listdir(path)
file_list

['each_personal_essay_538.json',
 'each_personal_essay_492.json',
 'each_personal_essay_168.json',
 'each_personal_essay_884.json',
 'each_personal_essay_187.json',
 'each_personal_essay_50.json',
 'each_personal_essay_304.json',
 'each_personal_essay_754.json',
 'each_personal_essay_241.json',
 'each_personal_essay_611.json',
 'each_personal_essay_580.json',
 'each_personal_essay_979.json',
 'each_personal_essay_703.json',
 'each_personal_essay_353.json',
 'each_personal_essay_646.json',
 'each_personal_essay_216.json',
 'each_personal_essay_579.json',
 'each_personal_essay_129.json',
 'each_personal_essay_980.json',
 'each_personal_essay_596.json',
 'each_personal_essay_11.json',
 'each_personal_essay_345.json',
 'each_personal_essay_715.json',
 'each_personal_essay_200.json',
 'each_personal_essay_650.json',
 'each_personal_essay_484.json',
 'each_personal_essay_191.json',
 'each_personal_essay_938.json',
 'each_personal_essay_892.json',
 'each_personal_essay_742.json',
 'each_perso

In [16]:
from tqdm import tqdm

In [17]:
essay_results = []

for file_name_raw in tqdm(file_list): # 파일이름을 하나씩 불러와서
    file_name = path  + file_name_raw #경로를 추가하고
    with open(file_name, 'r') as json_file : #JSON파일로 파일을 열어서
        ps_input_each_data = json.load(json_file) # JSON파일로 로드한다.
        input_data = json.dumps(ps_input_each_data)
        re_each_ess = FeatureExtration(input_data, winSize=10, step=10)
        essay_results.append(re_each_ess)

  0%|          | 1/981 [00:00<11:14,  1.45it/s]

slideingWinows it : <str_iterator object at 0x7fa712abb3d0>
TTratio 표현다양성:  0.57
HonoreMeasureR 표현다양성 : 563.1211781821365
hapax 표현다양성 : 0.5627240143369175
YuleK 다양성지수: 3386.13
SimpsonIndex 다양성지수 0.99
Shannon 다양성지수: 8.69
vowels numbers: 1
vowels numbers: 2
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 3
vowels

  0%|          | 2/981 [00:01<11:19,  1.44it/s]

slideingWinows it : <str_iterator object at 0x7fa712abd350>
TTratio 표현다양성:  0.53
HonoreMeasureR 표현다양성 : 599.396142730657
hapax 표현다양성 : 0.45885286783042395
YuleK 다양성지수: 2511.18
SimpsonIndex 다양성지수 0.99
Shannon 다양성지수: 7.97
vowels numbers: 1
vowels numbers: 2
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels

  0%|          | 3/981 [00:03<16:13,  1.00it/s]

...

slideingWinows it : <str_iterator object at 0x7fa720d47150>
TTratio 표현다양성:  0.46
HonoreMeasureR 표현다양성 : 526.7858159063328
hapax 표현다양성 : 0.38144329896907214
YuleK 다양성지수: 2124.56
SimpsonIndex 다양성지수 0.98
Shannon 다양성지수: 8.0
vowels numbers: 1
vowels numbers: 2
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels

100%|█████████▉| 980/981 [16:58<00:00,  1.17it/s]

slideingWinows it : <str_iterator object at 0x7fa720d230d0>
TTratio 표현다양성:  0.5
HonoreMeasureR 표현다양성 : 575.890177387728
hapax 표현다양성 : 0.4384858044164038
YuleK 다양성지수: 2295.77
SimpsonIndex 다양성지수 0.99
Shannon 다양성지수: 7.46
vowels numbers: 1
vowels numbers: 2
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 3
vowels n

100%|██████████| 981/981 [16:59<00:00,  1.04s/it]

slideingWinows it : <str_iterator object at 0x7fa7144c1e50>
TTratio 표현다양성:  0.46
HonoreMeasureR 표현다양성 : 580.2118375377063
hapax 표현다양성 : 0.40483383685800606
YuleK 다양성지수: 1974.06
SimpsonIndex 다양성지수 0.99
Shannon 다양성지수: 8.4
vowels numbers: 1
vowels numbers: 2
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 4
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels numbers: 5
vowels numbers: 1
vowels numbers: 1
vowels numbers: 1
vowels

In [18]:
essay_results

[[[0.57, 563.1211781821365, 0.5627240143369175, 3386.13, 0.99, 8.69, 42.06],
  [0.63, 599.8936561946682, 0.5558312655086849, 3341.32, 0.99, 8.69, 25.07],
  [0.58, 585.2202479774475, 0.5086206896551724, 2878.19, 0.99, 8.69, 40.24],
  [0.62, 572.0311776607412, 0.5081967213114754, 3014.46, 0.99, 8.69, 38.3],
  [0.57, 608.6774726912306, 0.525, 2946.59, 0.99, 8.69, 25.08],
  [0.57, 576.5191102784844, 0.4670846394984326, 2726.39, 0.99, 8.69, 40.26]],
 [[0.53, 599.396142730657, 0.45885286783042395, 2511.18, 0.99, 7.97, 39.76],
  [0.59, 582.8945617610208, 0.5235294117647059, 2997.06, 0.99, 7.97, 34.23]],
 [[0.5, 553.7334267018537, 0.44881889763779526, 2507.6, 0.99, 9.0, 57.82],
  [0.54, 552.5452939131784, 0.46613545816733065, 2563.77, 0.99, 9.0, 56.65],
  [0.59, 526.2690188904886, 0.49222797927461137, 2904.24, 0.99, 9.0, 69.77],
  [0.65, 517.0483995038152, 0.5965909090909091, 3914.64, 0.99, 9.0, 72.17],
  [0.55, 528.3203728737989, 0.41116751269035534, 2419.03, 0.99, 9.0, 80.34],
  [0.58, 532.3

In [20]:
extracted_features_result = essay_results

In [41]:
result = []
for i in extracted_features_result:
    for k in i:
        result.append(k)
    
result

[[0.57, 563.1211781821365, 0.5627240143369175, 3386.13, 0.99, 8.69, 42.06],
 [0.63, 599.8936561946682, 0.5558312655086849, 3341.32, 0.99, 8.69, 25.07],
 [0.58, 585.2202479774475, 0.5086206896551724, 2878.19, 0.99, 8.69, 40.24],
 [0.62, 572.0311776607412, 0.5081967213114754, 3014.46, 0.99, 8.69, 38.3],
 [0.57, 608.6774726912306, 0.525, 2946.59, 0.99, 8.69, 25.08],
 [0.57, 576.5191102784844, 0.4670846394984326, 2726.39, 0.99, 8.69, 40.26],
 [0.53, 599.396142730657, 0.45885286783042395, 2511.18, 0.99, 7.97, 39.76],
 [0.59, 582.8945617610208, 0.5235294117647059, 2997.06, 0.99, 7.97, 34.23],
 [0.5, 553.7334267018537, 0.44881889763779526, 2507.6, 0.99, 9.0, 57.82],
 [0.54, 552.5452939131784, 0.46613545816733065, 2563.77, 0.99, 9.0, 56.65],
 [0.59, 526.2690188904886, 0.49222797927461137, 2904.24, 0.99, 9.0, 69.77],
 [0.65, 517.0483995038152, 0.5965909090909091, 3914.64, 0.99, 9.0, 72.17],
 [0.55, 528.3203728737989, 0.41116751269035534, 2419.03, 0.99, 9.0, 80.34],
 [0.58, 532.3009979138409, 0.

In [12]:
result = [[0.57, 563.1211781821365, 0.5627240143369175, 3386.13, 0.99, 8.69, 42.06],
 [0.63, 599.8936561946682, 0.5558312655086849, 3341.32, 0.99, 8.69, 25.07],
 [0.58, 585.2202479774475, 0.5086206896551724, 2878.19, 0.99, 8.69, 40.24],
 [0.62, 572.0311776607412, 0.5081967213114754, 3014.46, 0.99, 8.69, 38.3],
 [0.57, 608.6774726912306, 0.525, 2946.59, 0.99, 8.69, 25.08],
 [0.57, 576.5191102784844, 0.4670846394984326, 2726.39, 0.99, 8.69, 40.26],
 [0.53, 599.396142730657, 0.45885286783042395, 2511.18, 0.99, 7.97, 39.76],
 [0.59, 582.8945617610208, 0.5235294117647059, 2997.06, 0.99, 7.97, 34.23],
 [0.5, 553.7334267018537, 0.44881889763779526, 2507.6, 0.99, 9.0, 57.82],
 [0.54, 552.5452939131784, 0.46613545816733065, 2563.77, 0.99, 9.0, 56.65],
 [0.59, 526.2690188904886, 0.49222797927461137, 2904.24, 0.99, 9.0, 69.77],
 [0.65, 517.0483995038152, 0.5965909090909091, 3914.64, 0.99, 9.0, 72.17],
 [0.55, 528.3203728737989, 0.41116751269035534, 2419.03, 0.99, 9.0, 80.34],
 [0.58, 532.3009979138409, 0.4975609756097561, 2824.03, 0.99, 9.0, 53.14],
 [0.59, 532.7876168789581, 0.48058252427184467, 2801.87, 0.99, 9.0, 71.76],
 [0.64, 537.9897353540459, 0.5668202764976958, 3643.31, 0.99, 9.0, 65.9],
 [0.61, 514.166355650266, 0.5321637426900585, 3336.41, 0.99, 9.0, 72.23],
 [0.6, 515.3291594497779, 0.5202312138728323, 3160.15, 0.99, 9.0, 76.31],
 [0.64, 559.0986980510856, 0.5298507462686567, 3207.01, 0.99, 9.0, 47.05],
 [0.61, 542.0534999272286, 0.5309734513274337, 3290.78, 0.99, 9.0, 39.78],
 [0.56, 566.9880922980519, 0.4482758620689655, 2457.79, 0.99, 9.0, 38.83],
 [0.58, 525.7495372027781, 0.46875, 2758.79, 0.99, 9.0, 44.58],
 [0.58, 563.1211781821365, 0.4982078853046595, 2805.46, 0.99, 9.0, 56.32],
 [0.54, 553.7334267018537, 0.42913385826771655, 2362.82, 0.99, 9.0, 54.15],
 [0.58, 567.3323267171493, 0.4948453608247423, 2760.24, 0.99, 9.0, 54.9],
 [0.6, 575.5742213586913, 0.5474683544303798, 3350.22, 0.99, 9.0, 48.13],
 [0.62, 499.0432586778736, 0.5102040816326531, 3228.28, 0.99, 9.0, 71.63],
 [0.62, 541.164605185504, 0.5446428571428571, 3435.91, 0.99, 9.0, 58.33],
 [0.62, 491.26548857360524, 0.5073529411764706, 3188.8, 0.99, 9.0, 64.89],
 [0.65, 509.3750200806762, 0.5398773006134969, 3298.58, 0.99, 9.0, 75.07],
 [0.57, 514.7494476813453, 0.4883720930232558, 2870.47, 0.99, 9.0, 69.85],
 [0.72, 488.28019225863704, 0.6818181818181818, 4838.15, 0.99, 9.0, 61.41],
 [0.57, 532.7876168789581, 0.5, 2910.74, 0.99, 9.0, 66.42],
 [0.51, 541.610040220442, 0.4711111111111111, 2588.05, 0.98, 7.68, 60.67],
 [0.58, 496.98132995760005, 0.5069444444444444, 2985.15, 0.99, 7.68, 79.42],
 [0.63, 517.0483995038152, 0.5454545454545454, 3342.59, 0.99, 7.68, 58.23],
 [0.61, 515.3291594497779, 0.5086705202312138, 3107.35, 0.99, 7.68, 73.38],
 [0.49, 550.5331535932362, 0.3861788617886179, 2093.66, 0.99, 7.52, 58.75],
 [0.56, 550.1258210544728, 0.40816326530612246, 2262.72, 0.99, 7.52, 55.93],
 [0.6, 537.0638028127662, 0.48372093023255813, 2876.8, 0.99, 7.52, 62.24],
 [0.58, 539.3627546352362, 0.41363636363636364, 2559.92, 0.99, 7.52, 59.53],
 [0.56, 550.1258210544728, 0.40816326530612246, 2262.72, 0.99, 7.52, 55.93],
 [0.6, 537.0638028127662, 0.48372093023255813, 2876.8, 0.99, 7.52, 62.24],
 [0.58, 539.3627546352362, 0.41363636363636364, 2559.92, 0.99, 7.52, 59.53],
 [0.57, 558.724865840025, 0.44569288389513106, 2406.26, 0.99, 7.52, 57.43],
 [0.55, 557.2154032177765, 0.4296577946768061, 2365.51, 0.99, 7.52, 46.97],
 [0.54, 538.9071729816501, 0.5205479452054794, 3014.12, 0.98, 8.82, 66.78],
 [0.62, 499.7212273764115, 0.5202702702702703, 3187.55, 0.99, 8.82, 75.2],
 [0.61, 503.0437921392435, 0.5098039215686274, 3100.52, 0.99, 8.82, 68.0],
 [0.61, 516.4785973923515, 0.5314285714285715, 3253.55, 0.99, 8.82, 59.51],
 [0.66, 524.1747015059642, 0.5978835978835979, 3910.86, 0.99, 8.82, 43.52],
 [0.6, 568.0172609017068, 0.4948805460750853, 2905.57, 0.99, 8.82, 40.23],
 [0.6, 519.295685089021, 0.49444444444444446, 3054.94, 0.99, 8.82, 72.01],
 [0.59, 540.2677381872279, 0.5180180180180181, 3049.27, 0.99, 8.82, 36.44],
 [0.57, 566.6426688112432, 0.46366782006920415, 2622.57, 0.99, 8.82, 27.91],
 [0.63, 511.7993812416755, 0.5688622754491018, 3637.28, 0.99, 8.82, 57.16],
 [0.59, 555.2959584921617, 0.5077519379844961, 2870.32, 0.99, 8.82, 43.91],
 [0.56, 588.887795833288, 0.45429362880886426, 2549.86, 0.99, 8.82, 36.15],
 [0.54, 577.7652323222657, 0.42724458204334365, 2237.15, 0.99, 8.82, 28.42],
 [0.55, 601.8593214496234, 0.4306569343065693, 2370.46, 0.99, 8.82, 29.47],
 [0.69, 485.9812404361672, 0.6201550387596899, 4254.55, 0.99, 8.82, 80.94],
 [0.61, 510.59454739005804, 0.503030303030303, 3165.47, 0.99, 8.82, 62.93],
 [0.63, 526.2690188904886, 0.5595854922279793, 3389.08, 0.99, 8.82, 62.76],
 [0.59, 571.0427017374869, 0.4867549668874172, 2814.57, 0.99, 8.82, 41.72],
 [0.69, 485.9812404361672, 0.6201550387596899, 4254.55, 0.99, 8.82, 80.94],
 [0.64, 503.0437921392435, 0.5424836601307189, 3445.68, 0.99, 8.82, 65.79],
 [0.6, 524.1747015059642, 0.5238095238095238, 3128.13, 0.99, 8.82, 57.84],
 [0.6, 560.947179518496, 0.5274725274725275, 3075.58, 0.99, 8.82, 43.39],
 [0.65, 545.10384535657, 0.575107296137339, 3624.68, 0.99, 8.82, 47.03],
 [0.58, 587.7735781779638, 0.48179271708683474, 2735.84, 0.99, 8.82, 31.5],
 [0.52, 604.5005314036013, 0.3886255924170616, 2026.12, 0.99, 8.82, 20.06],
 [0.59, 510.59454739005804, 0.48484848484848486, 2982.55, 0.99, 8.82, 61.91],
 [0.57, 548.4796933490654, 0.5477178423236515, 3258.55, 0.99, 8.66, 49.33],
 [0.62, 557.2154032177765, 0.5741444866920152, 3639.49, 0.99, 8.66, 46.32],
 [0.6, 544.673737166631, 0.5431034482758621, 3219.01, 0.99, 8.66, 51.28],
 [0.66, 578.0743515792329, 0.6049382716049383, 3816.49, 0.99, 8.66, 28.77],
 [0.57, 610.9247582764366, 0.49777777777777776, 2822.81, 0.99, 8.66, 23.17],
 [0.59, 566.6426688112432, 0.532871972318339, 3131.43, 0.99, 8.66, 49.87],
 [0.59, 576.8320995793772, 0.503125, 2813.67, 0.99, 8.66, 41.11],
 [0.44, 556.0681631015527, 0.3769230769230769, 1875.74, 0.98, 8.09, 63.63],
 [0.58, 556.8344503761097, 0.4847328244274809, 2733.23, 0.99, 8.09, 62.38],
 [0.65, 492.7253685157205, 0.5362318840579711, 3462.51, 0.99, 8.09, 61.64],
 [0.61, 561.6771097666572, 0.52, 3058.25, 0.99, 8.09, 44.49],
 [0.6, 521.4935757608986, 0.4673913043478261, 2761.7, 0.99, 8.09, 69.99],
 [0.49, 626.3398262591624, 0.4095238095238095, 2127.02, 0.99, 8.6, -10.33],
 [0.55, 580.2118375377063, 0.47129909365558914, 2604.03, 0.98, 8.6, 31.64],
 [0.64, 543.372200355424, 0.5764192139737991, 3731.43, 0.99, 8.6, 36.56],
 [0.61, 560.947179518496, 0.5128205128205128, 3086.05, 0.99, 8.6, 31.0],
 [0.66, 508.75963352323834, 0.5987654320987654, 3907.94, 0.99, 8.6, 61.4],
 [0.68, 475.35901911063644, 0.6206896551724138, 4186.98, 0.99, 8.6, 68.89],
 [0.62, 546.383180502561, 0.5847457627118644, 3697.57, 0.99, 8.6, 34.83],
 [0.56, 581.1140992976701, 0.44610778443113774, 2468.54, 0.99, 8.6, 1.2],
 [0.47, 640.1917196727186, 0.4096185737976783, 1974.32, 0.99, 8.57, 23.99],
 [0.59, 553.338948872752, 0.49407114624505927, 2813.98, 0.99, 8.57, 58.1],
 [0.57, 594.0171252720431, 0.4631578947368421, 2563.99, 0.99, 8.57, 17.99],
 [0.55, 551.3428746164982, 0.4798387096774194, 2640.15, 0.99, 8.57, 50.67],
 [0.62, 522.5746673713202, 0.5698924731182796, 3651.29, 0.99, 8.57, 56.05],
 [0.59, 570.7110264748875, 0.5116279069767442, 2963.98, 0.99, 8.57, 53.18],
 [0.6, 527.8114659230516, 0.5459183673469388, 3284.05, 0.99, 8.57, 61.77],
 [0.48, 562.4017506187339, 0.4404332129963899, 2379.54, 0.98, 8.98, 49.83],
 [0.51, 567.3323267171493, 0.4054982817869416, 2133.18, 0.99, 8.98, 32.23],
 [0.68, 537.9897353540459, 0.5852534562211982, 3758.41, 0.99, 8.98, 42.9],
 [0.58, 546.383180502561, 0.4957627118644068, 2831.08, 0.99, 8.98, 24.08],
 [0.61, 542.9345628954441, 0.5043859649122807, 3087.1, 0.99, 8.98, 45.66],
 [0.6, 552.5452939131784, 0.5059760956175299, 2952.65, 0.99, 8.98, 37.44],
 [0.56, 557.9729825986223, 0.4716981132075472, 2600.78, 0.99, 8.98, 33.4],
 [0.66, 518.7385805840755, 0.5698324022346368, 3679.04, 0.99, 8.98, 50.19],
 [0.67, 539.3627546352362, 0.5909090909090909, 3819.42, 0.99, 8.98, 17.61],
 [0.63, 540.2677381872279, 0.545045045045045, 3354.44, 0.99, 8.98, 18.53],
 [0.6, 573.9792912179234, 0.4758842443729904, 2648.44, 0.99, 8.98, 7.16],
 [0.67, 542.0534999272286, 0.588495575221239, 3837.42, 0.99, 8.98, 36.03],
 [0.55, 580.8142489980444, 0.45345345345345345, 2479.78, 0.99, 8.98, -6.07],
 [0.44, 530.8267697401205, 0.3613861386138614, 1867.95, 0.98, 7.62, 69.06],
 [0.56, 520.9486152841421, 0.45901639344262296, 2532.17, 0.99, 7.62, 62.52],
 [0.64, 519.8497031265827, 0.569060773480663, 3545.07, 0.99, 7.62, 52.92],
 [0.66, 500.3946305945459, 0.5369127516778524, 3401.65, 0.99, 7.62, 61.12],
 [0.54, 502.38805208462765, 0.42105263157894735, 2480.09, 0.99, 7.62, 75.08],
 [0.57, 527.2999558563747, 0.47692307692307695, 2629.85, 0.99, 7.62, 55.59],
 [0.66, 515.9055299214529, 0.5862068965517241, 3692.03, 0.99, 7.62, 55.47],
 [0.44, 536.5976015021852, 0.35046728971962615, 1949.08, 0.97, 7.88, 76.0],
 [0.56, 529.8317366548036, 0.43, 2395.0, 0.99, 7.88, 72.75],
 [0.48, 542.4950017481403, 0.3656387665198238, 1854.88, 0.98, 7.88, 70.12],
 [0.49, 578.9960170897253, 0.382262996941896, 1913.98, 0.99, 7.88, 48.94],
 [0.52, 584.6438775057725, 0.4421965317919075, 2291.59, 0.99, 7.88, 41.88],
 [0.51, 586.6468056933296, 0.49008498583569404, 2641.38, 0.99, 8.61, 35.84],
 [0.61, 585.5071922202427, 0.5157593123209169, 2966.15, 0.99, 8.61, 23.06],
 [0.6, 522.0355825078325, 0.4972972972972973, 2919.5, 0.99, 8.61, 40.81],
 [0.61, 510.59454739005804, 0.49696969696969695, 3016.35, 0.99, 8.61, 63.96],
 [0.56, 567.3323267171493, 0.46048109965635736, 2533.51, 0.99, 8.61, 35.72],
 [0.53, 559.4711379601839, 0.44981412639405205, 2487.8, 0.99, 8.61, 45.56],
 [0.66, 531.3205979041787, 0.5714285714285714, 3688.03, 0.99, 8.61, 44.95],
 [0.63, 556.0681631015527, 0.5423076923076923, 3357.1, 0.99, 8.61, 35.65],
 [0.53, 532.7876168789581, 0.5145631067961165, 3139.79, 0.98, 8.5, 67.65],
 [0.66, 480.40210447332566, 0.6311475409836066, 4342.92, 0.99, 8.5, 80.03],
 [0.63, 510.59454739005804, 0.5575757575757576, 3489.44, 0.99, 8.5, 78.83],
 [0.6, 535.6586274672012, 0.5283018867924528, 3216.0, 0.99, 8.5, 65.6],
 [0.59, 535.1858133476067, 0.4976303317535545, 2967.14, 0.99, 8.5, 44.28],
 [0.63, 532.7876168789581, 0.5533980582524272, 3479.12, 0.99, 8.5, 66.01],
 [0.6, 554.1263545158425, 0.5058823529411764, 3044.06, 0.99, 8.5, 48.58],
 [0.68, 532.3009979138409, 0.5951219512195122, 3847.71, 0.99, 8.5, 54.79],
 [0.54, 541.610040220442, 0.4488888888888889, 2474.27, 0.99, 8.5, 47.89],
 [0.51, 534.2334251964811, 0.47368421052631576, 2664.32, 0.98, 8.67, 65.81],
 [0.61, 535.6586274672012, 0.5188679245283019, 3119.88, 0.99, 8.67, 50.83],
 [0.58, 567.6753802268282, 0.4965753424657534, 2820.65, 0.99, 8.67, 47.11],
 [0.66, 541.610040220442, 0.5822222222222222, 3608.49, 0.99, 8.67, 46.01],
 [0.61, 562.4017506187339, 0.51985559566787, 3072.37, 0.99, 8.67, 50.75],
 [0.61, 554.907608489522, 0.5330739299610895, 3112.54, 0.99, 8.67, 38.21],
 [0.67, 527.2999558563747, 0.6, 3955.29, 0.99, 8.67, 32.59],
 [0.59, 558.724865840025, 0.48314606741573035, 2789.77, 0.99, 8.67, 54.58],
 [0.64, 521.4935757608986, 0.5597826086956522, 3394.97, 0.99, 8.67, 64.94],
 [0.63, 541.610040220442, 0.56, 3477.33, 0.99, 8.67, 51.65],
 [0.52, 582.600010738045, 0.46017699115044247, 2465.0, 0.99, 7.76, 44.9],
 [0.61, 550.5331535932362, 0.5284552845528455, 3126.45, 0.99, 7.76, 58.41],
 [0.5, 550.5331535932362, 0.44308943089430897, 2403.99, 0.99, 8.13, 57.37],
 [0.61, 533.7538079701318, 0.5240384615384616, 3048.26, 0.99, 8.13, 50.69],
 [0.59, 559.8421958998375, 0.5222222222222223, 3040.05, 0.99, 8.13, 50.96],
 [0.55, 511.7993812416755, 0.4251497005988024, 2428.2, 0.99, 8.13, 72.36],
 [0.55, 585.2202479774475, 0.4166666666666667, 2359.62, 0.99, 8.13, 37.08],
 [0.49, 564.1907070938114, 0.4219858156028369, 2196.32, 0.99, 7.96, 60.01],
 [0.55, 572.0311776607412, 0.46229508196721314, 2536.95, 0.99, 7.96, 53.83],
 [0.59, 511.7993812416755, 0.49700598802395207, 2928.75, 0.99, 7.96, 76.41],
 [0.59, 563.8354669333745, 0.5338078291814946, 3092.41, 0.99, 7.96, 45.54],
 [0.47, 514.7494476813453, 0.42441860465116277, 2291.78, 0.97, 7.92, 69.85],
 [0.54, 545.9585514144159, 0.4, 2268.54, 0.99, 7.92, 60.22],
 [0.55, 534.7107530717468, 0.42857142857142855, 2471.66, 0.98, 7.92, 63.86],
 [0.57, 564.1907070938114, 0.4787234042553192, 2641.97, 0.99, 7.92, 51.01],
 [0.51, 554.907608489522, 0.47470817120622566, 2566.28, 0.98, 9.11, 57.96],
 [0.62, 524.7024072160486, 0.5736842105263158, 3578.95, 0.99, 9.11, 50.85],
 [0.61, 553.338948872752, 0.5177865612648221, 3080.82, 0.99, 9.11, 37.7],
 [0.69, 521.4935757608986, 0.5815217391304348, 3872.28, 0.99, 9.11, 52.06],
 [0.61, 568.3579767338681, 0.5170068027210885, 3025.13, 0.99, 9.11, 29.66],
 [0.62, 556.0681631015527, 0.5384615384615384, 3507.99, 1.0, 9.11, 32.72],
 [0.67, 502.38805208462765, 0.6052631578947368, 4003.64, 0.99, 9.11, 60.61],
 [0.66, 539.8162701517753, 0.5972850678733032, 3833.66, 0.99, 9.11, 48.51],
 [0.65, 509.9866427824199, 0.5609756097560976, 3562.61, 0.99, 9.11, 64.32],
 [0.69, 496.2844630259907, 0.6293706293706294, 4212.43, 0.99, 9.11, 31.4],
 [0.6, 536.1292165709425, 0.5446009389671361, 3319.89, 0.99, 9.11, 31.9],
 [0.57, 570.3782474656201, 0.47, 2574.44, 0.99, 9.11, 32.28],
 [0.59, 574.3003187809483, 0.4935897435897436, 2805.51, 0.99, 9.11, 35.79],
 [0.57, 530.8267697401205, 0.48514851485148514, 2893.34, 0.99, 9.11, 35.98],
 [0.61, 545.5321115357701, 0.5427350427350427, 3234.35, 0.99, 9.11, 26.9],
 [0.59, 556.4520407322693, 0.5325670498084292, 3079.52, 0.99, 9.11, 38.37],
 [0.49, 568.3579767338681, 0.445578231292517, 2278.45, 0.99, 7.94, 44.34],
 [0.55, 551.7452896464707, 0.4457831325301205, 2485.44, 0.99, 7.94, 55.85],
 [0.57, 526.2690188904886, 0.49222797927461137, 2846.25, 0.99, 7.94, 65.39],
 [0.6, 542.9345628954441, 0.5526315789473685, 3358.73, 0.99, 7.94, 52.71],
 [0.53, 570.0443573390687, 0.48494983277591974, 2632.86, 0.99, 8.88, 54.82],
 [0.62, 529.3304824724493, 0.5577889447236181, 3374.66, 0.99, 8.88, 61.22],
 [0.64, 537.5278407684166, 0.5833333333333334, 3697.27, 0.99, 8.88, 49.39],
 [0.63, 541.610040220442, 0.5644444444444444, 3438.62, 0.99, 8.88, 47.89],
 [0.62, 540.7171771460119, 0.5291479820627802, 3122.52, 0.99, 8.88, 33.21],
 [0.61, 543.372200355424, 0.4890829694323144, 2832.14, 0.99, 8.88, 38.4],
 [0.59, 527.2999558563747, 0.5025641025641026, 2955.42, 0.99, 8.88, 62.53],
 [0.61, 535.6586274672012, 0.5235849056603774, 3248.93, 0.99, 8.88, 64.4],
 [0.61, 546.383180502561, 0.5466101694915254, 3239.73, 0.99, 8.88, 67.09],
 [0.61, 562.4017506187339, 0.5415162454873647, 3200.62, 0.99, 8.88, 44.34],
 [0.58, 564.8974238161206, 0.4964788732394366, 2802.77, 0.99, 8.88, 46.34],
 [0.59, 560.2118820879701, 0.4833948339483395, 2747.51, 0.99, 8.88, 46.97],
 [0.62, 557.5949103146316, 0.5681818181818182, 3457.3, 0.99, 8.88, 42.56],
 [0.57, 556.4520407322693, 0.47126436781609193, 2643.53, 0.99, 8.88, 42.58],
 [0.6, 554.5177444479563, 0.51171875, 2975.77, 0.99, 8.88, 47.67],
 [0.64, 547.2270673671475, 0.5714285714285714, 3633.92, 0.99, 8.88, 57.56],
 [0.62, 526.7858159063328, 0.5309278350515464, 3208.63, 0.99, 8.88, 68.09],
 [0.5, 582.0082930352362, 0.44807121661721067, 2278.26, 0.99, 8.25, 53.14],
 [0.5, 578.3825182329738, 0.37846153846153846, 1970.56, 0.99, 8.25, 52.02],
 [0.51, 607.5346031088684, 0.3954022988505747, 2034.61, 0.99, 8.25, 29.07],
 [0.46, 626.1491684321041, 0.3683206106870229, 1715.52, 0.99, 8.25, 23.84],
 [0.5, 591.350300563827, 0.37567567567567567, 1948.14, 0.99, 8.25, 24.55],
 [0.47, 576.2051382780177, 0.3081761006289308, 1681.9, 0.99, 8.25, 48.99],
 [0.51, 612.9050210060545, 0.4008714596949891, 2001.89, 0.99, 8.25, 24.96],
 [0.52, 560.947179518496, 0.4542124542124542, 2419.46, 0.99, 8.37, 49.59],
 [0.58, 548.4796933490654, 0.49377593360995853, 2791.62, 0.99, 8.37, 35.29],
 [0.65, 531.3205979041787, 0.5763546798029556, 3608.92, 0.99, 8.37, 54.54],
 [0.63, 512.9898714923073, 0.5502958579881657, 3525.79, 0.98, 8.37, 75.55],
 [0.62, 568.697535633982, 0.5186440677966102, 3079.8, 0.99, 8.37, 42.68],
 [0.55, 585.5071922202427, 0.4469914040114613, 2416.24, 0.99, 8.37, 36.63],
 [0.46, 574.3003187809483, 0.36217948717948717, 1730.36, 0.99, 6.94, 49.89],
 [0.49, 570.3782474656201, 0.3566666666666667, 1715.78, 0.99, 6.94, 50.05],
 [0.5, 568.697535633982, 0.3694915254237288, 1785.92, 0.99, 6.94, 52.14],
 [0.5, 570.3782474656201, 0.39, 1947.11, 0.99, 6.94, 51.18],
 [0.5, 525.227342804663, 0.47643979057591623, 2661.11, 0.98, 7.86, 66.53],
 [0.58, 528.8267030694535, 0.5404040404040404, 3288.44, 0.98, 7.86, 57.7],
 [0.68, 471.8498871295094, 0.625, 4271.36, 0.99, 7.86, 83.67],
 [0.62, 496.98132995760005, 0.5347222222222222, 3334.3, 0.99, 7.86, 80.01],
 [0.59, 537.5278407684166, 0.5416666666666666, 3286.18, 0.99, 7.86, 60.36],
 [0.51, 550.1258210544728, 0.4816326530612245, 2609.25, 0.98, 8.18, 66.64],
 [0.6, 499.7212273764115, 0.5135135135135135, 2946.49, 0.99, 8.18, 70.06],
 [0.57, 502.38805208462765, 0.5131578947368421, 3021.99, 0.98, 8.18, 73.41],
 [0.64, 511.19877883565437, 0.5481927710843374, 3345.91, 0.99, 8.18, 68.18],
 [0.55, 585.5071922202427, 0.42406876790830944, 2330.85, 0.99, 8.18, 37.36],
 [0.62, 526.2690188904886, 0.5440414507772021, 3277.4, 0.99, 8.18, 55.74],
 [0.6, 545.5321115357701, 0.5470085470085471, 3312.15, 0.99, 8.18, 57.63],
 [0.51, 545.10384535657, 0.4721030042918455, 2608.63, 0.98, 8.63, 60.46],
 [0.64, 508.1404364984463, 0.5962732919254659, 3862.51, 0.99, 8.63, 60.7],
 [0.66, 530.3304908059076, 0.582089552238806, 3729.12, 0.99, 8.63, 57.22],
 [0.63, 565.2489180268651, 0.5614035087719298, 3436.63, 0.99, 8.63, 17.61],
 [0.6, 581.7111159963204, 0.5357142857142857, 3075.22, 0.99, 8.63, 20.65],
 [0.6, 577.7652323222657, 0.5263157894736842, 3018.53, 0.99, 8.63, 27.38],
 [0.67, 523.1108616854586, 0.6310160427807486, 4210.01, 0.99, 8.63, 43.08],
 [0.63, 531.8119993844216, 0.5735294117647058, 3612.55, 0.99, 8.63, 58.4],
 [0.62, 549.3061443340548, 0.522633744855967, 3153.31, 0.99, 8.63, 39.43],
 [0.53, 531.8119993844216, 0.5441176470588235, 3232.89, 0.98, 8.36, 63.38],
 [0.69, 464.43908991413724, 0.6346153846153846, 4469.3, 0.99, 8.36, 58.8],
 [0.66, 506.2595033026967, 0.6708860759493671, 4639.48, 0.99, 8.36, 58.01],
 [0.63, 523.1108616854586, 0.5614973262032086, 3485.37, 0.99, 8.36, 64.35],
 [0.64, 538.9071729816501, 0.5570776255707762, 3454.47, 0.99, 8.36, 48.24],
 [0.61, 583.4810737062605, 0.5584795321637427, 3387.54, 0.99, 8.36, 17.02],
 [0.66, 572.6847747587196, 0.6026058631921825, 3914.95, 0.99, 8.36, 16.12],
 [0.48, 496.2844630259907, 0.5104895104895105, 2997.7, 0.97, 8.29, 72.22],
 [0.62, 519.8497031265827, 0.5303867403314917, 3156.8, 0.99, 8.29, 65.07],
 [0.62, 536.1292165709425, 0.5352112676056338, 3257.73, 0.99, 8.29, 55.73],
 [0.66, 495.5827057601261, 0.5774647887323944, 3768.1, 0.99, 8.29, 61.35],
 [0.68, 560.5802066295997, 0.6139705882352942, 3988.97, 0.99, 8.29, 37.4],
 [0.58, 567.3323267171493, 0.4948453608247423, 2697.89, 0.99, 8.29, 36.01],
 [0.5, 551.3428746164982, 0.4435483870967742, 2398.54, 0.99, 7.73, 49.99],
 [0.62, 545.5321115357701, 0.5641025641025641, 3471.4, 0.99, 7.73, 57.99],
 [0.65, 522.0355825078325, 0.6108108108108108, 3972.53, 0.99, 7.73, 62.76],
 [0.51, 579.6057750765372, 0.45896656534954405, 2365.09, 0.99, 7.92, 55.16],
 [0.63, 528.8267030694535, 0.51010101010101, 3144.58, 0.99, 7.92, 63.68],
 [0.58, 556.0681631015527, 0.47307692307692306, 2644.08, 0.99, 7.92, 45.74],
 [0.52, 564.5446897643237, 0.4558303886925795, 2473.75, 0.99, 8.29, 54.65],
 [0.56, 549.7168225293202, 0.4385245901639344, 2415.35, 0.99, 8.29, 46.15],
 [0.6, 562.7621113690636, 0.4892086330935252, 2867.35, 0.99, 8.29, 47.15],
 [0.53, 593.2245187448011, 0.41379310344827586, 2178.3, 0.99, 8.29, 15.75],
 [0.55, 589.715386763674, 0.45879120879120877, 2496.08, 0.99, 8.29, 36.71],
 [0.48, 581.7111159963204, 0.4107142857142857, 2088.47, 0.99, 7.67, 60.18],
 [0.61, 569.37321388027, 0.5420875420875421, 3244.11, 0.99, 7.67, 47.94],
 [0.52, 564.8974238161206, 0.4964788732394366, 2776.73, 0.99, 8.48, 48.73],
 [0.61, 518.7385805840755, 0.5195530726256983, 3063.57, 0.99, 8.48, 52.55],
 [0.69, 512.9898714923073, 0.6568047337278107, 4605.58, 0.99, 8.48, 48.01],
 [0.56, 578.0743515792329, 0.49074074074074076, 2744.44, 0.99, 8.48, 33.47],
 [0.62, 522.5746673713202, 0.553763440860215, 3368.6, 0.99, 8.48, 66.97],
 [0.55, 573.3341276897746, 0.4854368932038835, 2632.15, 0.99, 8.48, 47.61],
 [0.56, 570.0443573390687, 0.4816053511705686, 2698.85, 0.99, 8.48, 41.52],
 [0.49, 545.5321115357701, 0.42735042735042733, 2294.91, 0.98, 7.06, 55.46],
 [0.51, 588.6104031450155, 0.4527777777777778, 2348.61, 0.99, 7.62, 12.85],
 [0.6, 549.3061443340548, 0.49794238683127573, 2876.26, 0.99, 7.62, 33.86],
 [0.49, 548.0638923341991, 0.42083333333333334, 2191.67, 0.98, 8.44, 56.99],
 [0.65, 508.75963352323834, 0.5493827160493827, 3545.19, 0.99, 8.44, 48.35],
 [0.63, 534.2334251964811, 0.5645933014354066, 3459.17, 0.99, 8.44, 58.92],
 [0.58, 561.312810638807, 0.5182481751824818, 2967.39, 0.99, 8.44, 47.8],
 [0.56, 556.4520407322693, 0.4482758620689655, 2535.49, 0.99, 8.44, 64.63],
 [0.63, 485.9812404361672, 0.5038759689922481, 3202.93, 0.99, 8.44, 80.29],
 [0.66, 504.3425116919247, 0.6193548387096774, 4117.38, 0.99, 8.44, 40.46],
 [0.55, 564.8974238161206, 0.4507042253521127, 2428.83, 0.99, 8.44, 49.02],
 [0.6, 550.9388336627977, 0.5141700404858299, 2914.32, 0.99, 8.44, 54.69],
 [0.65, 500.3946305945459, 0.5570469798657718, 3521.46, 0.99, 8.44, 62.82],
 [0.65, 510.59454739005804, 0.5575757575757576, 3578.33, 0.99, 8.44, 43.96],
 [0.59, 536.5976015021852, 0.5186915887850467, 2978.43, 0.99, 8.44, 60.59],
 [0.54, 568.3579767338681, 0.47278911564625853, 2666.71, 0.99, 8.15, 45.2],
 [0.59, 578.0743515792329, 0.5216049382716049, 3075.37, 0.99, 8.15, 36.6],
 [0.64, 531.3205979041787, 0.5566502463054187, 3359.95, 0.99, 8.15, 45.79],
 [0.62, 528.3203728737989, 0.5634517766497462, 3431.68, 0.99, 8.15, 66.6],
 [0.52, 567.3323267171493, 0.46048109965635736, 2468.09, 0.99, 8.3, 41.53],
 [0.58, 560.947179518496, 0.5091575091575091, 2936.58, 0.99, 8.3, 43.39],
 [0.61, 561.6771097666572, 0.5381818181818182, 3228.3, 0.99, 8.3, 48.18],
 [0.57, 573.6572297479192, 0.45161290322580644, 2510.72, 0.99, 8.3, 36.46],
 [0.52, 584.354441703136, 0.4144927536231884, 2154.17, 0.99, 8.3, 41.36],
 [0.57, 572.3585101952381, 0.5686274509803921, 3431.8, 0.99, 9.28, 47.49],
 [0.63, 552.9429087511423, 0.5992063492063492, 3745.59, 0.99, 9.28, 41.26],
 [0.63, 563.1211781821365, 0.5878136200716846, 3726.83, 0.99, 9.28, 48.74],
 [0.61, 557.2154032177765, 0.5285171102661597, 3180.9, 0.99, 9.28, 35.71],
 [0.61, 562.4017506187339, 0.631768953068592, 4230.21, 0.99, 9.28, 21.74],
 [0.65, 563.4789603169249, 0.6178571428571429, 4043.88, 0.99, 9.28, 18.28],
 [0.68, 535.6586274672012, 0.6226415094339622, 4115.79, 0.99, 9.28, 38.46],
 [0.67, 537.0638028127662, 0.6186046511627907, 4048.03, 0.99, 9.28, 47.69],
 [0.72, 520.4006687076795, 0.6538461538461539, 4466.85, 0.99, 9.28, 45.66],
 [0.64, 539.8162701517753, 0.5158371040723982, 3216.56, 0.99, 9.28, 50.42],
 [0.65, 541.610040220442, 0.5866666666666667, 3740.44, 0.99, 9.28, 53.9],
 [0.62, 545.5321115357701, 0.5555555555555556, 3389.95, 0.99, 9.28, 31.96],
 [0.58, 576.8320995793772, 0.50625, 2866.99, 0.99, 9.28, 37.67],
 [0.63, 538.4495062789089, 0.536697247706422, 3228.26, 0.99, 9.28, 30.25],
 [0.61, 548.8937726156687, 0.5454545454545454, 3194.45, 0.99, 9.28, 32.3],
 [0.68, 534.2334251964811, 0.6172248803827751, 4070.88, 0.99, 9.28, 33.02],
 [0.7, 528.3203728737989, 0.6091370558375635, 4033.09, 0.99, 9.28, 37.82],
 [0.71, 511.7993812416755, 0.6407185628742516, 4352.97, 0.99, 9.28, 58.68],
 [0.68, 522.5746673713202, 0.6505376344086021, 4575.1, 0.99, 9.28, 45.14],
 [0.6, 554.907608489522, 0.5486381322957199, 3303.91, 0.99, 9.28, 27.35],
 [0.57, 581.1140992976701, 0.46107784431137727, 2529.13, 0.99, 9.28, 12.35],
 [0.5, 596.6146739123692, 0.4512820512820513, 2356.87, 0.99, 7.49, 36.45],
 [0.54, 605.6784013228624, 0.477751756440281, 2649.72, 0.99, 7.49, 21.44],
 [0.58, 577.4551545544408, 0.5186335403726708, 2993.52, 0.99, 7.49, 37.79],
 [0.56, 586.0786223465866, 0.48717948717948717, 2768.48, 0.99, 7.49, 37.68],
 [0.5, 589.715386763674, 0.44505494505494503, 2314.03, 0.99, 7.86, 33.92],
 [0.58, 566.2960480135946, 0.4791666666666667, 2724.01, 0.99, 7.86, 33.96],
 [0.52, 580.5134968916489, 0.39759036144578314, 2048.19, 0.99, 7.86, 30.69],
 [0.52, 559.0986980510856, 0.48134328358208955, 2613.33, 0.99, 8.28, 46.1],
 [0.58, 540.7171771460119, 0.47085201793721976, 2666.45, 0.99, 8.28, 58.63],
 [0.61, 538.4495062789089, 0.5091743119266054, 3164.3, 0.99, 8.28, 52.76],
 [0.59, 532.3009979138409, 0.5170731707317073, 2978.7, 0.99, 8.28, 56.45],
 [0.58, 528.8267030694535, 0.4797979797979798, 2693.09, 0.99, 8.28, 45.74],
 [0.54, 556.4520407322693, 0.42528735632183906, 2357.57, 0.99, 8.28, 53.61],
 [0.63, 519.8497031265827, 0.5414364640883977, 3248.37, 0.99, 8.28, 54.32],
 [0.51, 566.6426688112432, 0.4602076124567474, 2653.94, 0.99, 8.88, 59.53],
 [0.65, 490.527477843843, 0.5851851851851851, 3957.2, 0.99, 8.88, 78.45],
 [0.58, 553.7334267018537, 0.5039370078740157, 2937.88, 0.99, 8.88, 56.82],
 [0.67, 548.8937726156687, 0.5991735537190083, 3958.4, 0.99, 8.88, 49.43],
 [0.62, 538.4495062789089, 0.5321100917431193, 3165.56, 0.99, 8.88, 50.05],
 [0.61, 530.8267697401205, 0.5396039603960396, 3360.45, 0.99, 8.88, 49.38],
 [0.6, 520.4006687076795, 0.5054945054945055, 2977.3, 0.99, 8.88, 58.67],
 [0.63, 550.5331535932362, 0.573170731707317, 3604.34, 0.99, 8.88, 62.19],
 [0.64, 542.0534999272286, 0.588495575221239, 3680.79, 0.99, 8.88, 51.38],
 [0.61, 520.4006687076795, 0.532967032967033, 3247.8, 0.99, 8.88, 58.21],
 [0.58, 543.372200355424, 0.49344978165938863, 2992.32, 0.99, 8.88, 55.03],
 [0.62, 520.4006687076795, 0.5659340659340659, 3558.15, 0.99, 8.88, 52.63],
 [0.55, 568.697535633982, 0.43728813559322033, 2321.86, 0.99, 8.88, 26.62],
 [0.57, 588.6104031450155, 0.4888888888888889, 2787.96, 0.99, 8.88, 28.83],
 [0.66, 514.7494476813453, 0.5988372093023255, 3841.94, 0.99, 8.88, 55.1],
 [0.6, 558.724865840025, 0.4943820224719101, 2894.7, 0.99, 8.88, 36.83],
 [0.61, 536.5976015021852, 0.5093457943925234, 2963.14, 0.99, 8.88, 54.66],
 [0.65, 527.2999558563747, 0.6, 3871.66, 0.99, 8.88, 59.06],
 [0.61, 538.9071729816501, 0.54337899543379, 3294.34, 0.99, 8.88, 43.99],
 [0.62, 543.372200355424, 0.5633187772925764, 3412.22, 0.99, 8.88, 53.92],
 [0.64, 532.7876168789581, 0.558252427184466, 3449.9, 0.99, 8.88, 54.1],
 [0.6, 548.8937726156687, 0.5206611570247934, 3055.8, 0.99, 8.88, 50.48],
 [0.57, 559.4711379601839, 0.483271375464684, 2632.08, 0.99, 8.88, 49.01],
 [0.61, 560.2118820879701, 0.5350553505535055, 3251.05, 0.99, 8.88, 22.3],
 [0.45, 573.9792912179234, 0.3504823151125402, 1934.02, 0.99, 8.71, 41.43],
 [0.5, 544.673737166631, 0.34913793103448276, 1869.05, 0.99, 8.71, 53.83],
 [0.56, 568.3579767338681, 0.445578231292517, 2553.8, 0.99, 8.71, 39.73],
 [0.54, 550.1258210544728, 0.44081632653061226, 2380.01, 0.99, 8.71, 38.67],
 [0.52, 546.383180502561, 0.4406779661016949, 2275.93, 0.98, 8.71, 59.21],
 [0.53, 552.9429087511423, 0.42857142857142855, 2403.31, 0.99, 8.71, 48.99],
 [0.59, 544.2417710521793, 0.4935064935064935, 2869.51, 0.99, 8.71, 55.21],
 [0.55, 509.9866427824199, 0.39634146341463417, 2248.66, 0.98, 8.71, 67.42],
 [0.57, 554.907608489522, 0.4474708171206226, 2551.14, 0.99, 8.71, 55.33],
 [0.6, 523.6441962829949, 0.48936170212765956, 2821.98, 0.99, 8.71, 50.05],
 [0.63, 523.6441962829949, 0.5159574468085106, 3185.83, 0.99, 8.71, 55.9],
 [0.51, 523.6441962829949, 0.40425531914893614, 2177.46, 0.99, 8.71, 54.55],
 [0.59, 533.7538079701318, 0.46634615384615385, 2715.42, 0.99, 8.71, 43.77],
 [0.56, 558.724865840025, 0.4307116104868914, 2501.93, 0.99, 8.71, 39.69],
 [0.57, 566.6426688112432, 0.4359861591695502, 2624.49, 0.99, 8.71, 36.99],
 [0.53, 580.8142489980444, 0.3783783783783784, 2023.28, 0.99, 8.71, 26.45],
 [0.54, 535.1858133476067, 0.46445497630331756, 2473.89, 0.99, 8.71, 45.89],
 [0.58, 540.7171771460119, 0.484304932735426, 2857.49, 0.99, 8.71, 60.9],
 [0.47, 552.5452939131784, 0.4103585657370518, 2126.0, 0.98, 7.6, 62.72],
 [0.57, 534.7107530717468, 0.4523809523809524, 2452.15, 0.99, 7.6, 63.86],
 [0.58, 536.1292165709425, 0.4835680751173709, 2754.74, 0.99, 7.6, 68.84],
 [0.55, 579.9092654460526, 0.5121212121212121, 2890.91, 0.99, 8.76, 17.98],
 [0.56, 583.1882477283517, 0.4604105571847507, 2507.89, 0.99, 8.76, 13.2],
 [0.67, 556.4520407322693, 0.5938697318007663, 3868.7, 0.99, 8.76, 28.97],
 [0.62, 543.372200355424, 0.5458515283842795, 3379.8, 0.99, 8.76, 27.69],
 [0.65, 519.8497031265827, 0.5469613259668509, 3528.59, 0.99, 8.76, 29.55],
 [0.61, 557.9729825986223, 0.5056603773584906, 2957.07, 0.99, 8.76, 20.95],
 [0.63, 540.2677381872279, 0.545045045045045, 3286.26, 0.99, 8.76, 47.11],
 [0.63, 537.5278407684166, 0.5601851851851852, 3416.92, 0.99, 8.76, 44.3],
 [0.6, 558.3496308781699, 0.5112781954887218, 3064.05, 0.99, 8.76, 30.04],
 [0.46, 583.1882477283517, 0.3812316715542522, 1962.83, 0.99, 9.3, 33.54],
 [0.49, 581.4130531825066, 0.33432835820895523, 1780.71, 0.99, 9.3, 22.07],
 [0.57, 551.3428746164982, 0.4798387096774194, 2671.7, 0.99, 9.3, 53.06],
 [0.55, 538.4495062789089, 0.43119266055045874, 2403.42, 0.99, 9.3, 48.88],
 [0.59, 581.4130531825066, 0.5134328358208955, 2948.54, 0.99, 9.3, 44.29],
 [0.58, 543.8079308923195, 0.4956521739130435, 2810.59, 0.99, 9.3, 59.53],
 [0.54, 572.0311776607412, 0.43934426229508194, 2420.85, 0.99, 9.3, 56.33],
 [0.62, 568.3579767338681, 0.5544217687074829, 3448.33, 0.99, 9.3, 53.55],
 [0.55, 573.3341276897746, 0.4692556634304207, 2591.93, 0.99, 9.3, 46.52],
 [0.53, 593.4894195619588, 0.4417989417989418, 2345.54, 0.99, 9.3, 37.32],
 [0.54, 567.3323267171493, 0.436426116838488, 2298.04, 0.99, 9.3, 35.43],
 [0.49, 613.7727054086234, 0.36069114470842334, 1787.48, 0.99, 9.3, 18.96],
 [0.54, 562.4017506187339, 0.4259927797833935, 2307.86, 0.99, 9.3, 46.47],
 [0.55, 574.6203190540153, 0.46325878594249204, 2504.67, 0.99, 9.3, 32.35],
 [0.54, 572.6847747587196, 0.4234527687296417, 2411.06, 0.99, 9.3, 30.45],
 [0.57, 563.4789603169249, 0.5107142857142857, 2930.1, 0.99, 9.3, 30.97],
 [0.54, 589.715386763674, 0.4532967032967033, 2420.3, 0.99, 9.3, 34.62],
 [0.49, 576.8320995793772, 0.346875, 1880.27, 0.99, 9.3, 40.85],
 [0.57, 535.1858133476067, 0.44549763033175355, 2587.54, 0.99, 9.3, 43.08],
 [0.54, 559.4711379601839, 0.4758364312267658, 2607.21, 0.99, 9.3, 41.78],
 [0.52, 580.5134968916489, 0.4186746987951807, 2192.81, 0.99, 9.3, 30.69],
 [0.55, 556.4520407322693, 0.421455938697318, 2401.02, 0.99, 9.3, 32.21],
 [0.58, 559.8421958998375, 0.4925925925925926, 2807.13, 0.99, 9.3, 41.88],
 [0.53, 581.4130531825066, 0.43283582089552236, 2293.43, 0.99, 9.3, 28.63],
 [0.59, 549.7168225293202, 0.48360655737704916, 2878.26, 0.99, 9.3, 45.11],
 [0.54, 580.2118375377063, 0.4561933534743202, 2438.64, 0.99, 9.3, 38.03],
 [0.55, 569.035945432406, 0.46283783783783783, 2564.6, 0.99, 9.3, 37.32],
 [0.6, 539.3627546352362, 0.55, 3274.38, 0.99, 9.3, 48.76],
 [0.52, 571.3732805509369, 0.38943894389438943, 2052.74, 0.99, 9.3, 50.44],
 [0.61, 543.372200355424, 0.5283842794759825, 3117.03, 0.99, 9.3, 54.66],
 [0.59, 540.7171771460119, 0.4977578475336323, 2861.11, 0.99, 9.3, 49.52],
 [0.57, 537.0638028127662, 0.5023255813953489, 2843.05, 0.99, 9.3, 59.88],
 [0.57, 563.1211781821365, 0.4910394265232975, 2779.26, 0.99, 9.3, 46.01],
 [0.51, 566.2960480135946, 0.4444444444444444, 2411.99, 0.99, 8.24, 53.05],
 [0.53, 605.4439346269371, 0.4225352112676056, 2191.8, 0.99, 8.24, 33.32],
 [0.6, 527.8114659230516, 0.5204081632653061, 3061.75, 0.99, 8.24, 63.93],
 [0.54, 606.1456918928017, 0.42424242424242425, 2224.29, 0.99, 8.24, 34.72],
 [0.63, 520.9486152841421, 0.5737704918032787, 3590.43, 0.99, 8.24, 64.37],
 [0.55, 599.396142730657, 0.4488778054862843, 2373.12, 0.99, 8.24, 36.39],
 [0.59, 560.5802066295997, 0.47058823529411764, 2762.22, 0.99, 8.24, 51.39],
 [0.59, 532.3009979138409, 0.5024390243902439, 2899.7, 0.99, 8.24, 58.51],
 [0.63, 473.61984483944957, 0.5614035087719298, 3634.96, 0.99, 8.24, 86.92],
 [0.59, 527.8114659230516, 0.4897959183673469, 2938.36, 0.99, 8.24, 66.95],
 [0.52, 579.6057750765372, 0.44680851063829785, 2332.76, 0.99, 8.43, 47.18],
 [0.56, 574.3003187809483, 0.4583333333333333, 2483.77, 0.99, 8.43, 57.76],
 [0.56, 574.6203190540153, 0.43450479233226835, 2356.26, 0.99, 8.43, 46.14],
 [0.55, 564.8974238161206, 0.4154929577464789, 2169.46, 0.99, 8.43, 45.15],
 [0.54, 570.7110264748875, 0.38870431893687707, 2200.42, 0.99, 8.43, 40.53],
 [0.58, 564.8974238161206, 0.4612676056338028, 2642.08, 0.99, 8.43, 40.39],
 [0.63, 547.2270673671475, 0.5462184873949579, 3285.43, 0.99, 8.43, 52.58],
 [0.59, 539.8162701517753, 0.5339366515837104, 3142.85, 0.99, 8.43, 44.68],
 [0.54, 563.4789603169249, 0.425, 2271.94, 0.99, 8.43, 40.94],
 [0.52, 554.907608489522, 0.4669260700389105, 2561.43, 0.99, 8.35, 52.7],
 [0.71, 493.44739331306914, 0.6690647482014388, 4741.99, 0.99, 8.35, 60.04],
 [0.63, 531.3205979041787, 0.5665024630541872, 3523.99, 0.99, 8.35, 59.54],
 [0.64, 511.19877883565437, 0.608433734939759, 3848.89, 0.99, 8.35, 54.42],
 [0.69, 516.4785973923515, 0.7142857142857143, 5241.47, 0.99, 8.35, 43.08],
 [0.62, 569.035945432406, 0.5472972972972973, 3299.17, 0.99, 8.35, 42.75],
 [0.46, 512.9898714923073, 0.34911242603550297, 2067.85, 0.97, 8.7, 78.05],
 [0.57, 521.4935757608986, 0.4782608695652174, 2766.42, 0.99, 8.7, 54.82],
 [0.57, 534.7107530717468, 0.5, 2926.53, 0.99, 8.7, 59.43],
 [0.59, 521.4935757608986, 0.5108695652173914, 3045.25, 0.99, 8.7, 63.1],
 [0.62, 509.3750200806762, 0.5644171779141104, 3562.05, 0.99, 8.7, 47.04],
 [0.61, 509.9866427824199, 0.5121951219512195, 3008.63, 0.99, 8.7, 46.27],
 [0.57, 542.0534999272286, 0.49557522123893805, 2760.59, 0.99, 8.7, 34.16],
 [0.65, 515.9055299214529, 0.603448275862069, 3836.04, 0.99, 8.7, 26.78],
 [0.62, 535.1858133476067, 0.5308056872037915, 3295.97, 0.99, 8.7, 35.06],
 [0.67, 452.17885770490403, 0.6521739130434783, 4551.04, 0.99, 8.7, 66.0],
 [0.71, 443.0816798843313, 0.6904761904761905, 4997.17, 0.99, 8.7, 60.33],
 [0.62, 506.2595033026967, 0.5632911392405063, 3459.38, 0.99, 8.7, 36.59],
 [0.6, 539.3627546352362, 0.5363636363636364, 3228.51, 0.99, 8.7, 52.22],
 [0.65, 504.3425116919247, 0.5741935483870968, 3649.53, 0.99, 8.7, 54.65],
 [0.57, 522.5746673713202, 0.478494623655914, 2676.03, 0.99, 8.7, 31.49],
 [0.48, 527.2999558563747, 0.4307692307692308, 2286.92, 0.98, 8.45, 70.34],
 [0.6, 482.0281565605037, 0.47580645161290325, 2868.11, 0.98, 8.45, 83.72],
 [0.62, 501.0635294096256, 0.56, 3414.22, 0.99, 8.45, 66.4],
 [0.57, 505.6245805348308, 0.47770700636942676, 2732.77, 0.98, 8.45, 71.27],
 [0.61, 517.6149732573829, 0.559322033898305, 3448.56, 0.99, 8.45, 65.08],
 [0.58, 539.8162701517753, 0.4841628959276018, 2773.49, 0.99, 8.45, 55.78],
 [0.6, 535.6586274672012, 0.5330188679245284, 3202.21, 0.99, 8.45, 62.01],
 [0.64, 539.3627546352362, 0.5772727272727273, 3647.52, 0.99, 8.45, 51.84],
 [0.55, 532.3009979138409, 0.45365853658536587, 2631.29, 0.98, 8.45, 65.52],
 [0.56, 520.9486152841421, 0.453551912568306, 2498.73, 0.99, 8.45, 62.52],
 [0.62, 536.1292165709425, 0.5211267605633803, 3070.38, 0.99, 8.45, 52.16],
 [0.61, 530.8267697401205, 0.594059405940594, 3790.8, 0.99, 8.45, 66.97],
 [0.58, 512.9898714923073, 0.4970414201183432, 2896.96, 0.99, 8.45, 74.04],
 [0.52, 552.1460917862246, 0.4, 2105.28, 0.98, 8.45, 46.78],
 [0.45, 557.9729825986223, 0.35471698113207545, 1791.38, 0.98, 8.01, 60.86],
 [0.6, 478.7491742782046, 0.5666666666666667, 3481.94, 0.99, 8.01, 69.87],
 [0.6, 511.19877883565437, 0.5301204819277109, 3126.72, 0.98, 8.01, 71.24],
 [0.6, 537.0638028127662, 0.5162790697674419, 3038.18, 0.99, 8.01, 41.39],
 [0.62, 503.0437921392435, 0.5620915032679739, 3486.69, 0.99, 8.01, 56.94],
 [0.7, 484.4187086458591, 0.6141732283464567, 4155.25, 0.99, 8.01, 71.37],
 [0.63, 464.43908991413724, 0.5192307692307693, 3337.65, 0.99, 8.01, 79.14],
 [0.51, 549.7168225293202, 0.5, 2877.25, 0.98, 6.9, 58.29],
 [0.49, 553.338948872752, 0.42292490118577075, 2172.82, 0.98, 8.87, 53.42],
 [0.66, 504.9856007249537, 0.5705128205128205, 3608.65, 0.99, 8.87, 64.64],
 [0.59, 550.9388336627977, 0.5060728744939271, 2984.15, 0.99, 8.87, 65.65],
 [0.64, 526.2690188904886, 0.5129533678756477, 3084.65, 0.99, 8.87, 51.8],
 [0.54, 558.3496308781699, 0.39473684210526316, 2263.84, 0.99, 8.87, 52.94],
 [0.61, 540.2677381872279, 0.5, 2997.73, 0.99, 8.87, 45.59],
 [0.61, 496.98132995760005, 0.5, 2990.93, 0.99, 8.87, 58.27],
 [0.63, 532.3009979138409, 0.5609756097560976, 3451.75, 0.99, 8.87, 66.35],
 [0.62, 540.7171771460119, 0.5067264573991032, 2997.45, 0.99, 8.87, 59.39],
 [0.56, 560.947179518496, 0.43223443223443225, 2385.92, 0.99, 8.87, 51.14],
 [0.67, 530.3304908059076, 0.6069651741293532, 3956.34, 0.99, 8.87, 46.28],
 [0.6, 528.8267030694535, 0.5, 2983.88, 0.99, 8.87, 64.54],
 [0.62, 553.338948872752, 0.5454545454545454, 3269.23, 0.99, 8.87, 56.09],
 [0.56, 563.1211781821365, 0.4444444444444444, 2354.54, 0.99, 8.87, 52.07],
 [0.58, 551.7452896464707, 0.46586345381526106, 2595.76, 0.99, 8.87, 37.5],
 [0.56, 541.164605185504, 0.48214285714285715, 2661.03, 0.99, 8.87, 65.89],
 [0.55, 562.7621113690636, 0.4172661870503597, 2310.44, 0.99, 8.87, 56.89],
 [0.64, 519.295685089021, 0.5388888888888889, 3362.35, 0.99, 8.87, 56.03],
 [0.57, 515.3291594497779, 0.45664739884393063, 2716.43, 0.99, 8.87, 45.5],
 [0.46, 539.3627546352362, 0.37272727272727274, 1868.18, 0.97, 8.87, 72.22],
 [0.55, 505.6245805348308, 0.4713375796178344, 2581.04, 0.98, 8.87, 80.97],
 [0.6, 510.59454739005804, 0.47878787878787876, 3006.8, 0.99, 8.87, 62.42],
 [0.61, 526.7858159063328, 0.5, 3009.35, 0.99, 8.87, 72.45],
 [0.52, 538.9071729816501, 0.4794520547945205, 2772.67, 0.98, 7.0, 51.72],
 [0.5, 555.6828061699538, 0.47876447876447875, 2607.0, 0.98, 8.29, 44.99],
 [0.52, 594.8034989180645, 0.4412532637075718, 2295.74, 0.99, 8.29, 26.37],
 [0.6, 565.9482215759622, 0.5296167247386759, 3095.34, 0.99, 8.29, 35.62],
 [0.59, 555.6828061699538, 0.4980694980694981, 2815.1, 0.99, 8.29, 37.8],
 [0.55, 573.3341276897746, 0.4336569579288026, 2312.71, 0.99, 8.29, 47.34],
 [0.58, 542.9345628954441, 0.4956140350877193, 2863.57, 0.99, 8.29, 57.16],
 [0.5, 548.4796933490654, 0.46887966804979253, 2561.94, 0.98, 8.47, 50.73],
 [0.71, 520.4006687076795, 0.6263736263736264, 4241.03, 0.99, 8.47, 56.35],
 [0.63, 526.7858159063328, 0.5773195876288659, 3690.62, 0.99, 8.47, 50.21],
 [0.56, 530.8267697401205, 0.44554455445544555, 2579.16, 0.99, 8.47, 55.24],
 [0.58, 547.6463551931511, 0.4435146443514644, 2554.58, 0.99, 8.47, 44.17],
 [0.6, 531.3205979041787, 0.49261083743842365, 2871.7, 0.99, 8.47, 42.04],
 [0.59, 546.383180502561, 0.4745762711864407, 2716.53, 0.99, 8.47, 33.4],
 [0.64, 541.610040220442, 0.56, 3363.16, 0.99, 8.47, 50.52],
 [0.59, 560.5802066295997, 0.5110294117647058, 2920.63, 0.99, 8.47, 37.4],
 [0.56, 512.9898714923073, 0.4970414201183432, 2887.15, 0.99, 8.47, 62.53],
 [0.59, 512.9898714923073, 0.5384615384615384, 3238.68, 0.99, 8.47, 58.53],
 [0.51, 554.1263545158425, 0.4588235294117647, 2487.66, 0.98, 8.15, 49.24],
 [0.64, 525.227342804663, 0.5602094240837696, 3511.42, 0.99, 8.15, 52.35],
 [0.56, 563.4789603169249, 0.45357142857142857, 2532.65, 0.99, 8.15, 49.7],
 [0.58, 578.3825182329738, 0.5415384615384615, 3155.88, 0.99, 8.15, 39.79],
 [0.55, 570.7110264748875, 0.4485049833887043, 2447.43, 0.99, 8.15, 43.62],
 [0.5, 641.6732282512326, 0.45098039215686275, 2298.9, 0.99, 8.54, 6.07],
 [0.58, 646.6144724237619, 0.5069984447900466, 2822.02, 0.99, 8.54, -26.18],
 [0.54, 604.7372179046278, 0.4491725768321513, 2351.99, 0.99, 8.54, -14.1],
 [0.51, 558.3496308781699, 0.4548872180451128, 2442.48, 0.98, 8.59, 64.07],
 [0.6, 559.8421958998375, 0.5407407407407407, 3152.54, 0.99, 8.59, 46.89],
 [0.6, 543.8079308923195, 0.5652173913043478, 3463.89, 0.99, 8.59, 43.72],
 [0.63, 540.2677381872279, 0.6171171171171171, 3971.67, 0.99, 8.59, 23.87],
 [0.68, 518.7385805840755, 0.6201117318435754, 4061.05, 0.99, 8.59, 44.52],
 [0.55, 619.2362489474872, 0.5439672801635992, 3309.2, 1.0, 8.59, 6.69],
 [0.52, 519.295685089021, 0.5, 2872.84, 0.98, 8.88, 63.55],
 [0.64, 497.67337424205743, 0.593103448275862, 3767.9, 0.99, 8.88, 63.18],
 [0.66, 475.35901911063644, 0.5689655172413793, 3772.29, 0.99, 8.88, 78.37],
 [0.53, 525.227342804663, 0.44502617801047123, 2394.67, 0.98, 8.88, 73.17],
 [0.69, 508.1404364984463, 0.6273291925465838, 4191.97, 0.99, 8.88, 62.28],
 [0.58, 557.9729825986223, 0.4867924528301887, 2712.99, 0.99, 8.88, 31.81],
 [0.63, 551.3428746164982, 0.5685483870967742, 3500.91, 0.99, 8.88, 40.44],
 [0.6, 523.6441962829949, 0.4946808510638298, 2972.5, 0.99, 8.88, 35.65],
 [0.61, 548.8937726156687, 0.5289256198347108, 3162.35, 0.98, 8.88, 45.23],
 [0.62, 541.610040220442, 0.49777777777777776, 2900.15, 0.99, 8.88, 38.11],
 [0.59, 549.3061443340548, 0.4897119341563786, 2768.89, 0.99, 8.88, 36.64],
 [0.67, 518.7385805840755, 0.6033519553072626, 3876.91, 0.99, 8.88, 54.44],
 [0.65, 482.0281565605037, 0.5806451612903226, 3743.5, 0.99, 8.88, 73.49],
 [0.58, 545.10384535657, 0.4892703862660944, 2820.46, 0.99, 8.88, 50.66],
 [0.6, 527.8114659230516, 0.5357142857142857, 3205.96, 0.99, 8.88, 60.04],
 [0.48, 560.947179518496, 0.40293040293040294, 2100.66, 0.98, 8.88, 57.96],
 [0.56, 546.383180502561, 0.4830508474576271, 2708.27, 0.99, 8.88, 47.02],
 [0.64, 528.8267030694535, 0.5959595959595959, 3834.3, 0.99, 8.88, 44.03],
 [0.62, 494.87598903781685, 0.5460992907801419, 3316.73, 0.99, 8.88, 57.52],
 [0.65, 496.2844630259907, 0.5734265734265734, 3680.38, 0.99, 8.88, 58.03],
 [0.64, 527.2999558563747, 0.5435897435897435, 3385.14, 0.99, 8.88, 52.12],
 [0.59, 506.2595033026967, 0.5379746835443038, 3299.15, 0.98, 8.88, 52.65],
 [0.52, 539.3627546352362, 0.509090909090909, 3104.55, 0.98, 8.31, 47.61],
 [0.64, 553.338948872752, 0.5770750988142292, 3630.43, 0.99, 8.31, 31.35],
 [0.55, 588.6104031450155, 0.4666666666666667, 2455.86, 0.99, 8.31, 28.59],
 [0.59, 570.7110264748875, 0.5448504983388704, 3240.36, 0.99, 8.31, 32.1],
 [0.52, 547.6463551931511, 0.46443514644351463, 2709.34, 0.99, 8.45, 56.92],
 [0.59, 567.6753802268282, 0.5308219178082192, 3086.41, 0.99, 8.45, 47.4],
 [0.67, 514.7494476813453, 0.6511627906976745, 4424.69, 0.99, 8.45, 50.18],
 [0.68, 472.7387818712341, 0.5929203539823009, 3889.11, 0.99, 8.45, 65.1],
 [0.65, 466.3439094112067, 0.5660377358490566, 3812.74, 0.99, 8.45, 72.37],
 [0.57, 540.7171771460119, 0.484304932735426, 2726.78, 0.99, 8.45, 55.97],
 [0.62, 540.2677381872279, 0.5135135135135135, 3066.31, 0.99, 8.45, 59.69],
 [0.61, 556.0681631015527, 0.5461538461538461, 3238.46, 0.99, 8.45, 49.32],
 [0.48, 550.1258210544728, 0.4122448979591837, 2213.74, 0.98, 8.81, 62.49],
 [0.66, 533.2718793265369, 0.5748792270531401, 3744.31, 0.99, 8.81, 43.19],
 [0.63, 504.3425116919247, 0.5548387096774193, 3500.52, 0.99, 8.81, 72.12],
 [0.64, 530.3304908059076, 0.572139303482587, 3549.91, 0.99, 8.81, 58.9],
 [0.56, 553.7334267018537, 0.44881889763779526, 2415.83, 0.99, 8.81, 50.49],
 [0.64, 571.0427017374869, 0.543046357615894, 3269.81, 0.99, 8.81, 38.08],
 [0.57, 575.5742213586913, 0.4620253164556962, 2574.51, 0.99, 8.81, 24.03],
 [0.59, 560.2118820879701, 0.4870848708487085, 2829.48, 0.99, 8.81, 40.1],
 [0.63, 528.3203728737989, 0.5583756345177665, 3453.32, 0.99, 8.81, 52.85],
 [0.6, 501.72798368149245, 0.4768211920529801, 2942.85, 0.99, 8.81, 69.37],
 [0.7, 525.7495372027781, 0.65625, 4479.71, 0.99, 8.81, 48.99],
 [0.61, 527.8114659230516, 0.5255102040816326, 3147.13, 0.99, 8.81, 32.42],
 [0.49, 546.8060141135131, 0.43037974683544306, 2336.52, 0.98, 8.28, 63.91],
 [0.59, 533.2718793265369, 0.45893719806763283, 2751.99, 0.99, 8.28, 50.14],
 [0.55, 554.5177444479563, 0.39453125, 2233.28, 0.99, 8.28, 47.01],
 [0.59, 508.1404364984463, 0.4906832298136646, 2887.23, 0.99, 8.28, 63.33],
 [0.53, 539.8162701517753, 0.4072398190045249, 2196.11, 0.99, 8.28, 60.37],
 [0.53, 557.9729825986223, 0.4377358490566038, 2373.23, 0.99, 8.28, 39.47],
 [0.5, 529.8317366548036, 0.355, 2012.0, 0.99, 8.28, 47.79],
 [0.57, 548.4796933490654, 0.43568464730290457, 2372.2, 0.99, 8.28, 66.18],
 [0.63, 525.227342804663, 0.5340314136125655, 3475.23, 0.99, 8.28, 60.77],
 [0.55, 561.6771097666572, 0.4109090909090909, 2191.34, 0.99, 8.28, 38.95],
 [0.52, 559.8421958998375, 0.4962962962962963, 2753.64, 0.99, 9.42, 46.89],
 [0.69, 524.1747015059642, 0.6455026455026455, 4372.78, 0.99, 9.42, 39.94],
 [0.58, 580.5134968916489, 0.5180722891566265, 2988.1, 0.99, 9.42, 35.53],
 [0.63, 566.6426688112432, 0.5640138408304498, 3479.84, 0.99, 9.42, 35.23],
 [0.6, 559.0986980510856, 0.5708955223880597, 3440.08, 0.99, 9.42, 50.21],
 [0.67, 532.7876168789581, 0.6310679611650486, 4167.69, 0.99, 9.42, 48.35],
 [0.63, 548.4796933490654, 0.5435684647302904, 3329.49, 0.99, 9.42, 46.17],
 [0.61, 568.0172609017068, 0.5563139931740614, 3379.65, 0.99, 9.42, 34.46],
 [0.64, 550.9388336627977, 0.582995951417004, 3641.1, 0.99, 9.42, 50.93],
 [0.77, 423.41065045972596, 0.782608695652174, 6301.2, 1.0, 9.42, 67.41],
 [0.71, 467.28288344619057, 0.7102803738317757, 5200.45, 0.99, 9.42, 63.94],
 [0.69, 427.6666119016055, 0.7222222222222222, 5848.77, 1.0, 9.42, 82.03],
 [0.65, 477.912349311153, 0.5798319327731093, 3919.21, 0.99, 9.42, 59.68],
 [0.71, 468.213122712422, 0.6574074074074074, 4573.05, 0.99, 9.42, 71.32],
 [0.68, 512.3963979403259, 0.6011904761904762, 3959.75, 0.99, 9.42, 52.31],
 [0.67, 533.7538079701318, 0.6634615384615384, 4604.75, 0.99, 9.42, 44.18],
 [0.66, 541.610040220442, 0.6177777777777778, 4124.84, 0.99, 9.42, 41.49],
 [0.65, 514.7494476813453, 0.5872093023255814, 3848.7, 0.99, 9.42, 61.0],
 [0.66, 526.2690188904886, 0.616580310880829, 4085.48, 0.99, 9.42, 45.22],
 [0.58, 579.3013608384144, 0.5274390243902439, 3036.51, 0.99, 9.42, 14.92],
 [0.64, 504.9856007249537, 0.532051282051282, 3296.35, 0.99, 9.42, 60.3],
 [0.67, 509.9866427824199, 0.6280487804878049, 4187.98, 0.99, 9.42, 46.27],
 [0.56, 577.1441123130015, 0.48286604361370716, 2632.54, 0.99, 9.42, 20.08],
 [0.65, 537.5278407684166, 0.5462962962962963, 3433.21, 0.99, 9.42, 41.56],
 [0.67, 513.5798437050262, 0.5764705882352941, 3792.39, 0.99, 9.42, 57.7],
 [0.64, 518.7385805840755, 0.5698324022346368, 3591.02, 0.99, 9.42, 58.22],
 [0.66, 526.7858159063328, 0.5876288659793815, 3813.37, 0.99, 9.42, 44.11],
 [0.67, 499.0432586778736, 0.6122448979591837, 4082.56, 0.99, 9.42, 58.97],
 [0.63, 515.9055299214529, 0.603448275862069, 3984.67, 0.99, 9.42, 61.3],
 [0.64, 537.9897353540459, 0.5852534562211982, 3683.66, 0.99, 9.42, 61.22],
 [0.62, 544.673737166631, 0.5732758620689655, 3573.5, 0.99, 9.42, 51.28],
 [0.61, 548.4796933490654, 0.5352697095435685, 3164.2, 0.99, 9.42, 58.11],
 [0.57, 537.5278407684166, 0.5, 2838.22, 0.99, 9.42, 61.14],
 [0.67, 506.8904202220232, 0.6477987421383647, 4402.52, 0.99, 9.42, 61.4],
 [0.63, 550.5331535932362, 0.5772357723577236, 3665.81, 0.99, 9.42, 42.24],
 [0.61, 534.7107530717468, 0.5190476190476191, 3165.99, 0.99, 9.42, 57.01],
 [0.59, 572.6847747587196, 0.50814332247557, 2992.71, 0.99, 9.42, 41.75],
 [0.42, 607.3044534100405, 0.315668202764977, 1495.68, 0.99, 7.98, 51.48],
 [0.48, 575.890177387728, 0.36908517350157727, 1892.94, 0.99, 7.98, 63.37],
 [0.6, 566.2960480135946, 0.5069444444444444, 2899.55, 0.99, 7.98, 53.35],
 [0.58, 563.1211781821365, 0.4838709677419355, 2720.67, 0.99, 7.98, 55.1],
 [0.48, 559.8421958998375, 0.3851851851851852, 2009.6, 0.98, 8.34, 50.65],
 [0.59, 550.1258210544728, 0.4897959183673469, 2802.17, 0.99, 8.34, 37.63],
 [0.53, 580.5134968916489, 0.4036144578313253, 2175.21, 0.99, 8.34, 30.44],
 [0.59, 554.1263545158425, 0.49411764705882355, 2875.51, 0.99, 8.34, 42.27],
 [0.61, 543.8079308923195, 0.508695652173913, 2956.52, 0.99, 8.34, 51.44],
 [0.59, 579.6057750765372, 0.48328267477203646, 2729.83, 0.99, 8.34, 32.01],
 [0.49, 575.5742213586913, 0.439873417721519, 2368.61, 0.99, 8.19, 50.27],
 [0.6, 551.7452896464707, 0.5622489959839357, 3434.14, 0.99, 8.19, 53.47],
 [0.58, 554.5177444479563, 0.53125, 3098.14, 0.99, 8.19, 48.66],
 [0.63, 555.6828061699538, 0.5714285714285714, 3529.76, 0.99, 8.19, 41.4],
 [0.51, 567.3323267171493, 0.44329896907216493, 2342.2, 0.99, 7.87, 56.07],
 [0.51, 572.3585101952381, 0.38562091503267976, 2030.84, 0.99, 7.87, 59.11],
 [0.58, 497.67337424205743, 0.43448275862068964, 2422.83, 0.99, 7.87, 77.18],
 [0.6, 525.7495372027781, 0.5052083333333334, 2906.9, 0.99, 7.87, 67.06],
 [0.57, 530.8267697401205, 0.45544554455445546, 2506.13, 0.99, 7.87, 65.3],
 [0.52, 534.7107530717468, 0.4238095238095238, 2507.48, 0.98, 8.73, 67.08],
 [0.64, 551.3428746164982, 0.5645161290322581, 3475.87, 0.99, 8.73, 47.94],
 [0.59, 568.3579767338681, 0.47619047619047616, 2797.21, 0.99, 8.73, 51.53],
 [0.61, 553.7334267018537, 0.531496062992126, 3200.76, 0.99, 8.73, 51.49],
 [0.54, 554.5177444479563, 0.41796875, 2267.76, 0.99, 8.73, 47.34],
 [0.63, 550.5331535932362, 0.556910569105691, 3394.14, 0.99, 8.73, 49.46],
 [0.59, 553.7334267018537, 0.49606299212598426, 2846.43, 0.99, 8.73, 48.82],
 [0.62, 571.7027701406222, 0.506578947368421, 2940.18, 0.99, 8.73, 35.72],
 [0.58, 588.887795833288, 0.49584487534626037, 2804.46, 0.99, 8.73, 29.35],
 [0.55, 597.1261839790462, 0.44387755102040816, 2396.27, 0.99, 8.73, 26.55],
 [0.6, 573.9792912179234, 0.5369774919614148, 3208.4, 0.99, 8.73, 33.54],
 [0.63, 536.5976015021852, 0.5607476635514018, 3473.67, 0.99, 8.73, 55.84],
 [0.52, 554.5177444479563, 0.4453125, 2460.02, 0.99, 8.58, 60.56],
 [0.56, 557.9729825986223, 0.43018867924528303, 2405.7, 0.99, 8.58, 52.88],
 [0.6, 561.6771097666572, 0.5163636363636364, 2932.89, 0.99, 8.58, 42.64],
 [0.55, 520.4006687076795, 0.45604395604395603, 2607.78, 0.99, 8.58, 63.32],
 [0.65, 511.19877883565437, 0.5542168674698795, 3434.46, 0.99, 8.58, 46.78],
 [0.68, 512.3963979403259, 0.6190476190476191, 4069.59, 0.99, 8.58, 43.24],
 [0.54, 526.2690188904886, 0.46632124352331605, 2647.05, 0.98, 8.58, 57.5],
 [0.64, 529.3304824724493, 0.5577889447236181, 3461.53, 0.99, 8.58, 62.92],
 [0.58, 525.227342804663, 0.4712041884816754, 2596.42, 0.99, 8.58, 71.84],
 [0.62, 524.7024072160486, 0.5, 3102.49, 0.99, 8.58, 43.28],
 [0.68, 517.0483995038152, 0.5909090909090909, 3771.31, 0.99, 8.58, 40.92],
 [0.63, 515.3291594497779, 0.5375722543352601, 3252.36, 0.99, 8.58, 62.13],
 [0.65, 515.3291594497779, 0.5491329479768786, 3355.27, 0.99, 8.58, 65.07],
 [0.66, 504.3425116919247, 0.567741935483871, 3562.12, 0.99, 8.58, 60.65],
 [0.7, 506.2595033026967, 0.5949367088607594, 3967.31, 0.99, 8.58, 48.91],
 [0.57, 536.5976015021852, 0.45794392523364486, 2463.97, 0.99, 8.58, 38.45],
 [0.44, 534.7107530717468, 0.34285714285714286, 1903.4, 0.98, 7.62, 60.23],
 [0.6, 528.3203728737989, 0.5228426395939086, 3104.95, 0.99, 7.62, 51.14],
 [0.47, 578.6897381366708, 0.41411042944785276, 2315.29, 0.95, 7.62, 50.48],
 [0.57, 532.3009979138409, 0.45365853658536587, 2571.33, 0.99, 7.62, 53.56],
 [0.59, 519.8497031265827, 0.5303867403314917, 3109.8, 0.99, 7.62, 64.13],
 [0.53, 579.9092654460526, 0.48787878787878786, 2691.09, 0.99, 8.81, 47.21],
 [0.58, 573.9792912179234, 0.5273311897106109, 3076.68, 0.99, 8.81, 28.65],
 [0.57, 562.7621113690636, 0.5071942446043165, 2995.19, 0.99, 8.81, 35.89],
 [0.61, 544.673737166631, 0.5301724137931034, 3320.82, 0.99, 8.81, 35.97],
 [0.6, 548.8937726156687, 0.5289256198347108, 3069.8, 0.99, 8.81, 26.01],
 [0.57, 564.1907070938114, 0.48226950354609927, 2732.01, 0.99, 8.81, 20.71],
 [0.63, 546.383180502561, 0.5550847457627118, 3418.92, 0.99, 8.81, 40.21],
 [0.58, 545.9585514144159, 0.502127659574468, 2874.78, 0.99, 8.81, 41.5],
 [0.59, 558.724865840025, 0.5205992509363296, 3082.66, 0.99, 8.81, 30.18],
 [0.56, 539.3627546352362, 0.4636363636363636, 2602.07, 0.99, 8.81, 46.07],
 [0.54, 587.7735781779638, 0.45098039215686275, 2488.37, 0.99, 8.81, 21.07],
 [0.6, 568.697535633982, 0.5389830508474577, 3278.37, 0.99, 8.81, 29.49],
 [0.59, 542.4950017481403, 0.5330396475770925, 3119.41, 0.99, 8.81, 51.86],
 [0.59, 553.7334267018537, 0.5236220472440944, 3020.96, 0.99, 8.81, 44.49],
 [0.7, 524.7024072160486, 0.6473684210526316, 4412.19, 0.99, 8.81, 61.1],
 [0.46, 545.10384535657, 0.36909871244635195, 1879.2, 0.98, 8.32, 68.09],
 [0.6, 497.67337424205743, 0.4689655172413793, 3005.95, 0.99, 8.32, 73.68],
 [0.55, 515.3291594497779, 0.4624277456647399, 2526.65, 0.98, 8.32, 81.69],
 [0.6, 488.28019225863704, 0.5378787878787878, 3451.56, 0.99, 8.32, 73.59],
 [0.55, 550.1258210544728, 0.44081632653061226, 2550.27, 0.99, 8.32, 58.69],
 [0.47, 584.9324779946859, 0.3659942363112392, 1820.3, 0.99, 8.32, 43.62],
 [0.53, 570.7110264748875, 0.46511627906976744, 2433.09, 0.99, 8.32, 24.51],
 [0.51, 574.6203190540153, 0.38338658146964855, 1973.07, 0.99, 8.32, 39.11],
 [0.58, 562.0400865717149, 0.4673913043478261, 2617.1, 0.99, 8.32, 47.02],
 [0.43, 568.0172609017068, 0.3651877133105802, 1758.9, 0.98, 7.7, 40.23],
 [0.6, 504.9856007249537, 0.4807692307692308, 3038.3, 0.99, 7.7, 71.69],
 [0.63, 500.3946305945459, 0.5637583892617449, 3644.88, 0.99, 7.7, 75.88],
 [0.52, 566.9880922980519, 0.43448275862068964, 2227.59, 0.98, 7.7, 53.71],
 [0.44, 561.6771097666572, 0.3418181818181818, 1651.83, 0.98, 7.8, 57.41],
 [0.58, 536.5976015021852, 0.49065420560747663, 2804.61, 0.99, 7.8, 54.66],
 [0.58, 512.3963979403259, 0.48214285714285715, 2999.57, 0.99, 7.8, 44.75],
 [0.57, 552.5452939131784, 0.47808764940239046, 2661.86, 0.99, 7.8, 50.58],
 [0.55, 531.3205979041787, 0.4088669950738916, 2390.74, 0.99, 7.8, 52.45],
 [0.55, 550.1258210544728, 0.5224489795918368, 3015.74, 0.99, 7.61, 56.28],
 [0.67, 516.4785973923515, 0.5885714285714285, 3768.16, 0.99, 7.61, 48.39],
 [0.42, 535.1858133476067, 0.35071090047393366, 1840.93, 0.98, 7.93, 70.75],
 [0.52, 554.5177444479563, 0.3984375, 2107.24, 0.99, 7.93, 61.88],
 [0.57, 541.610040220442, 0.47555555555555556, 2618.86, 0.99, 7.93, 59.54],
 [0.53, 554.907608489522, 0.4474708171206226, 2405.18, 0.99, 7.93, 60.27],
 [0.58, 561.6771097666572, 0.4690909090909091, 2599.4, 0.99, 7.93, 49.41],
 [0.51, 522.0355825078325, 0.4702702702702703, 2629.07, 0.98, 7.92, 57.73],
 [0.6, 552.5452939131784, 0.50199203187251, 2909.16, 0.99, 7.92, 51.59],
 [0.55, 580.8142489980444, 0.43843843843843844, 2368.67, 0.99, 7.92, 35.85],
 [0.64, 526.7858159063328, 0.5670103092783505, 3465.83, 0.99, 7.92, 43.67],
 [0.52, 565.2489180268651, 0.5052631578947369, 2815.39, 0.98, 7.72, 55.31],
 [0.63, 547.6463551931511, 0.5899581589958159, 3711.07, 0.99, 7.72, 52.67],
 [0.5, 558.724865840025, 0.40074906367041196, 2265.15, 0.98, 8.09, 65.03],
 [0.64, 523.1108616854586, 0.5882352941176471, 3679.83, 0.99, 8.09, 53.49],
 [0.63, 514.7494476813453, 0.6046511627906976, 3868.98, 0.99, 8.09, 60.02],
 [0.57, 542.0534999272286, 0.504424778761062, 2853.39, 0.99, 8.09, 31.92],
 [0.56, 556.8344503761097, 0.4618320610687023, 2515.3, 0.99, 8.09, 22.02],
 [0.5, 577.4551545544408, 0.468944099378882, 2466.53, 0.99, 8.84, 35.17],
 [0.64, 538.9071729816501, 0.5753424657534246, 3640.87, 0.99, 8.84, 39.36],
 [0.53, 557.9729825986223, 0.42641509433962266, 2165.9, 0.99, 8.84, 53.2],
 [0.58, 534.7107530717468, 0.5190476190476191, 3002.72, 0.99, 8.84, 57.41],
 [0.56, 562.4017506187339, 0.4584837545126354, 2483.81, 0.99, 8.84, 54.11],
 [0.59, 537.0638028127662, 0.49767441860465117, 3065.87, 0.99, 8.84, 48.47],
 [0.61, 552.9429087511423, 0.5238095238095238, 3127.68, 0.99, 8.84, 49.66],
 [0.58, 550.1258210544728, 0.49795918367346936, 2931.11, 0.99, 8.84, 50.06],
 [0.58, 503.0437921392435, 0.5228758169934641, 3078.3, 0.99, 8.84, 63.02],
 [0.61, 539.8162701517753, 0.4841628959276018, 2910.26, 0.99, 8.84, 57.69],
 [0.66, 522.0355825078325, 0.6, 4098.76, 0.99, 8.84, 55.9],
 [0.62, 514.166355650266, 0.52046783625731, 3092.92, 0.99, 8.84, 49.47],
 [0.57, 533.7538079701318, 0.4423076923076923, 2399.69, 0.99, 8.84, 59.64],
 [0.54, 539.3627546352362, 0.39545454545454545, 2270.25, 0.99, 8.84, 54.53],
 [0.55, 594.8034989180645, 0.4516971279373368, 2454.17, 0.99, 8.84, 26.15],
 [0.59, 524.1747015059642, 0.48148148148148145, 2839.23, 0.99, 8.84, 49.78],
 [0.73, 420.46926193909655, 0.7611940298507462, 5930.05, 0.99, 8.84, 75.03],
 [0.6, 527.2999558563747, 0.5435897435897435, 3301.51, 0.99, 8.84, 39.97],
 [0.52, 545.10384535657, 0.463519313304721, 2536.43, 0.98, 8.83, 61.55],
 [0.62, 545.9585514144159, 0.5276595744680851, 3248.89, 0.99, 8.83, 53.02],
 [0.64, 516.4785973923515, 0.5542857142857143, 3453.39, 0.99, 8.83, 72.57],
 [0.6, 550.1258210544728, 0.5346938775510204, 3164.01, 0.99, 8.83, 60.07],
 [0.69, 492.7253685157205, 0.5869565217391305, 3961.35, 0.99, 8.83, 81.87],
 [0.61, 545.5321115357701, 0.5128205128205128, 3039.3, 0.99, 8.83, 54.38],
 [0.6, 540.7171771460119, 0.5246636771300448, 3015.54, 0.99, 8.83, 57.87],
 [0.69, 519.295685089021, 0.6333333333333333, 4291.98, 0.99, 8.83, 65.43],
 [0.63, 546.8060141135131, 0.5611814345991561, 3503.36, 0.99, 8.83, 36.07],
 [0.64, 503.695260241363, 0.6103896103896104, 4147.41, 0.99, 8.83, 75.84],
 [0.64, 499.0432586778736, 0.564625850340136, 3537.41, 0.99, 8.83, 62.42],
 [0.71, 467.28288344619057, 0.6448598130841121, 4571.58, 0.99, 8.83, 75.8],
 [0.62, 529.8317366548036, 0.52, 3137.5, 0.99, 8.83, 63.44],
 [0.66, 506.8904202220232, 0.6289308176100629, 4199.99, 0.99, 8.83, 57.15],
 [0.6, 539.3627546352362, 0.5272727272727272, 3109.5, 0.99, 8.83, 61.07],
 [0.58, 545.9585514144159, 0.44680851063829785, 2427.89, 0.99, 8.83, 40.78],
 [0.53, 551.3428746164982, 0.4032258064516129, 2301.64, 0.99, 8.83, 58.52],
 [0.61, 512.9898714923073, 0.5562130177514792, 3396.94, 0.99, 8.83, 72.54],
 [0.65, 526.7858159063328, 0.5876288659793815, 3844.19, 0.99, 8.83, 56.76],
 [0.6, 539.8162701517753, 0.5158371040723982, 3040.89, 0.99, 8.83, 44.3],
 [0.54, 563.4789603169249, 0.4142857142857143, 2218.37, 0.99, 8.83, 40.94],
 [0.63, 536.5976015021852, 0.5186915887850467, 3187.61, 0.99, 8.83, 57.03],
 [0.69, 480.40210447332566, 0.6065573770491803, 4118.52, 0.99, 8.83, 74.49],
 [0.62, 524.1747015059642, 0.5555555555555556, 3419.28, 0.99, 8.83, 65.9],
 [0.72, 483.6281906951478, 0.6428571428571429, 4487.28, 0.99, 8.83, 69.83],
 [0.62, 532.3009979138409, 0.5609756097560976, 3427.96, 0.99, 8.83, 64.7],
 [0.52, 578.0743515792329, 0.4567901234567901, 2419.41, 0.99, 7.79, 48.62],
 [0.61, 538.9071729816501, 0.5251141552511416, 3125.87, 0.99, 7.79, 55.58],
 [0.47, 588.05329864007, 0.4022346368715084, 2053.93, 0.99, 7.33, 56.36],
 [0.49, 538.4495062789089, 0.39908256880733944, 1990.15, 0.98, 7.33, 58.2],
 [0.48, 548.4796933490654, 0.42323651452282157, 2265.46, 0.98, 8.71, 61.62],
 [0.57, 537.0638028127662, 0.5023255813953489, 2877.66, 0.99, 8.71, 47.29],
 [0.53, 571.3732805509369, 0.44884488448844884, 2342.69, 0.99, 8.71, 44.85],
 [0.53, 574.3003187809483, 0.4551282051282051, 2462.4, 0.99, 8.71, 39.32],
 [0.58, 565.9482215759622, 0.4878048780487805, 2818.29, 0.99, 8.71, 35.62],
 [0.47, 569.035945432406, 0.36486486486486486, 1798.3, 0.99, 8.71, 45.6],
 [0.57, 551.7452896464707, 0.5542168674698795, 3332.53, 0.99, 8.71, 45.66],
 [0.55, 520.9486152841421, 0.4808743169398907, 2665.95, 0.99, 8.71, 58.36],
 [0.6, 532.7876168789581, 0.5339805825242718, 3241.59, 0.99, 8.71, 51.22],
 [0.57, 556.0681631015527, 0.4807692307692308, 2700.3, 0.99, 8.71, 45.09],
 [0.56, 569.7093486505405, 0.48322147651006714, 2678.03, 0.99, 8.71, 18.46],
 [0.52, 538.9071729816501, 0.4429223744292237, 2298.95, 0.99, 8.71, 60.6],
 [0.56, 537.5278407684166, 0.48148148148148145, 2711.33, 0.99, 8.71, 47.44],
 [0.6, 526.2690188904886, 0.48704663212435234, 2824.24, 0.99, 8.71, 62.32],
 [0.49, 536.1292165709425, 0.39436619718309857, 1954.2, 0.98, 8.71, 56.93],
 [0.52, 549.7168225293202, 0.47540983606557374, 2663.26, 0.98, 8.75, 64.18],
 [0.6, 539.3627546352362, 0.5363636363636364, 3131.4, 0.99, 8.75, 67.99],
 [0.56, 548.4796933490654, 0.4605809128630705, 2647.34, 0.98, 8.75, 68.99],
 [0.56, 543.372200355424, 0.4585152838427948, 2617.04, 0.99, 8.75, 60.57],
 [0.6, 524.1747015059642, 0.5079365079365079, 2956.8, 0.99, 8.75, 60.98],
 [0.57, 571.0427017374869, 0.5, 2912.15, 0.99, 8.75, 52.92],
 [0.6, 548.4796933490654, 0.5103734439834025, 3088.45, 0.99, 8.75, 51.79],
 [0.6, 571.0427017374869, 0.5165562913907285, 2992.63, 0.99, 8.75, 28.27],
 [0.56, 538.9071729816501, 0.45662100456621, 2499.53, 0.99, 8.75, 42.06],
 [0.6, 560.2118820879701, 0.5239852398523985, 3055.79, 0.99, 8.75, 27.3],
 [0.63, 532.3009979138409, 0.5219512195121951, 3176.68, 0.99, 8.75, 39.94],
 [0.66, 533.2718793265369, 0.5990338164251208, 3851.2, 0.99, 8.75, 47.28],
 [0.57, 524.1747015059642, 0.48148148148148145, 2866.66, 0.99, 8.75, 60.53],
 [0.55, 528.3203728737989, 0.467005076142132, 2499.94, 0.98, 8.75, 58.01],
 [0.55, 544.2417710521793, 0.44155844155844154, 2275.82, 0.99, 8.75, 42.02],
 [0.53, 567.6753802268282, 0.4931506849315068, 2810.56, 0.99, 8.19, 38.71],
 [0.58, 564.8974238161206, 0.5140845070422535, 3000.15, 0.99, 8.19, 28.47],
 [0.61, 542.9345628954441, 0.5394736842105263, 3267.54, 0.99, 8.19, 32.67],
 [0.61, 534.7107530717468, 0.5, 2867.57, 0.99, 8.19, 8.26],
 [0.48, 557.2154032177765, 0.4448669201520912, 2363.78, 0.99, 7.41, 50.51],
 [0.5, 533.7538079701318, 0.3894230769230769, 2040.03, 0.99, 7.41, 68.58],
 [0.51, 556.4520407322693, 0.4444444444444444, 2441.24, 0.99, 8.2, 65.92],
 [0.6, 546.8060141135131, 0.5485232067510548, 3346.33, 0.99, 8.2, 52.85],
 [0.58, 517.0483995038152, 0.48863636363636365, 2988.77, 0.99, 8.2, 64.96],
 [0.63, 549.7168225293202, 0.5450819672131147, 3286.08, 0.99, 8.2, 54.13],
 [0.62, 514.7494476813453, 0.5290697674418605, 3169.28, 0.99, 8.2, 68.87],
 [0.6, 507.51738152338265, 0.51875, 3217.19, 0.99, 8.2, 70.57],
 [0.62, 502.38805208462765, 0.5526315789473685, 3614.96, 0.99, 8.2, 67.29],
 [0.47, 550.1258210544728, 0.40816326530612246, 2115.12, 0.98, 8.49, 56.28],
 [0.57, 538.9071729816501, 0.5205479452054794, 2969.08, 0.99, 8.49, 58.67],
 [0.61, 534.2334251964811, 0.5311004784688995, 3170.71, 0.99, 8.49, 54.88],
 [0.61, 540.2677381872279, 0.5495495495495496, 3345.51, 0.99, 8.49, 50.54],
 [0.55, 563.4789603169249, 0.45714285714285713, 2501.02, 0.99, 8.49, 62.09],
 [0.55, 541.164605185504, 0.42857142857142855, 2479.67, 0.99, 8.49, 49.65],
 [0.52, 566.6426688112432, 0.3944636678200692, 2129.76, 0.99, 8.49, 50.46],
 [0.61, 552.1460917862246, 0.496, 2989.76, 0.99, 8.49, 48.47],
 [0.58, 550.9388336627977, 0.4898785425101215, 2898.59, 0.99, 8.49, 47.84],
 [0.51, 510.59454739005804, 0.503030303030303, 2894.4, 0.97, 9.29, 64.47],
 [0.66, 447.7336814478207, 0.6022727272727273, 3959.19, 0.99, 9.29, 71.0],
 [0.69, 461.512051684126, 0.6831683168316832, 4879.91, 0.99, 9.29, 73.45],
 [0.61, 541.164605185504, 0.5223214285714286, 3124.6, 0.99, 9.29, 57.58],
 [0.66, 516.4785973923515, 0.5885714285714285, 3934.69, 0.99, 9.29, 64.35],
 [0.64, 461.512051684126, 0.6039603960396039, 3911.38, 0.99, 9.29, 70.1],
 [0.57, 541.164605185504, 0.4732142857142857, 2706.07, 0.99, 9.29, 65.13],
 [0.58, 511.7993812416755, 0.49700598802395207, 3164.69, 0.99, 9.29, 60.2],
 [0.61, 528.8267030694535, 0.5505050505050505, 3351.7, 0.99, 9.29, 56.85],
 [0.62, 507.51738152338265, 0.54375, 3422.66, 0.99, 9.29, 64.22],
 [0.63, 523.1108616854586, 0.5508021390374331, 3462.5, 0.99, 9.29, 62.09],
 [0.67, 434.3805421853684, 0.6753246753246753, 4783.27, 0.99, 9.29, 101.24],
 [0.6, 519.8497031265827, 0.48066298342541436, 2794.79, 0.99, 9.29, 75.35],
 [0.61, 530.8267697401205, 0.5495049504950495, 3391.82, 0.99, 9.29, 64.46],
 [0.56, 546.383180502561, 0.5084745762711864, 2898.95, 0.99, 9.29, 46.66],
 [0.61, 549.7168225293202, 0.48770491803278687, 2900.43, 0.99, 9.29, 47.19],
 [0.66, 499.7212273764115, 0.5743243243243243, 3794.74, 0.99, 9.29, 66.63],
 [0.62, 510.59454739005804, 0.5575757575757576, 3527.64, 0.99, 9.29, 70.11],
 [0.61, 509.3750200806762, 0.5337423312883436, 3302.34, 0.99, 9.29, 58.98],
 [0.69, 418.9654742026425, 0.5909090909090909, 4012.86, 0.99, 9.29, 70.67],
 [0.67, 507.51738152338265, 0.60625, 4021.09, 0.99, 9.29, 55.24],
 [0.57, 510.59454739005804, 0.47878787878787876, 2765.84, 0.99, 9.29, 66.01],
 [0.59, 563.8354669333745, 0.5088967971530249, 2930.56, 0.99, 9.29, 45.54],
 [0.53, 571.0427017374869, 0.38741721854304634, 2143.33, 0.99, 9.29, 40.6],
 [0.58, 525.227342804663, 0.4973821989528796, 2856.28, 0.99, 9.29, 39.95],
 [0.67, 535.1858133476067, 0.5876777251184834, 3887.15, 0.99, 9.29, 57.92],
 [0.61, 508.1404364984463, 0.5217391304347826, 3350.18, 0.99, 9.29, 62.28],
 [0.55, 545.5321115357701, 0.44871794871794873, 2432.24, 0.99, 9.29, 51.12],
 [0.58, 544.2417710521793, 0.4675324675324675, 2642.0, 0.99, 9.29, 42.02],
 [0.55, 577.7652323222657, 0.4520123839009288, 2402.98, 0.99, 9.29, 40.73],
 [0.64, 397.0291913552122, 0.6415094339622641, 4371.66, 0.99, 9.29, 92.91],
 [0.61, 473.61984483944957, 0.5263157894736842, 3344.11, 0.99, 9.29, 88.4],
 [0.69, 511.7993812416755, 0.5988023952095808, 3959.27, 0.99, 9.29, 60.2],
 [0.64, 451.085950651685, 0.5714285714285714, 3789.4, 0.99, 9.29, 73.02],
 [0.61, 558.724865840025, 0.5131086142322098, 3079.86, 0.99, 9.29, 33.35],
 [0.61, 528.3203728737989, 0.5126903553299492, 3040.53, 0.99, 9.29, 49.85],
 [0.64, 514.166355650266, 0.5672514619883041, 3486.88, 0.99, 9.29, 62.33],
 [0.57, 538.4495062789089, 0.44495412844036697, 2581.85, 0.99, 9.29, 41.12],
 [0.71, 493.44739331306914, 0.6618705035971223, 4633.3, 0.99, 9.29, 49.7],
 [0.62, 550.5331535932362, 0.5528455284552846, 3414.63, 0.99, 9.29, 43.96],
 [0.69, 474.49321283632503, 0.6782608695652174, 4816.64, 0.99, 9.29, 66.42],
 [0.63, 506.8904202220232, 0.5471698113207547, 3335.31, 0.99, 9.29, 65.66],
 [0.64, 468.213122712422, 0.5740740740740741, 3743.14, 0.98, 9.29, 73.67],
 [0.63, 556.4520407322693, 0.5325670498084292, 3182.57, 0.99, 9.29, 41.61],
 [0.65, 512.9898714923073, 0.5680473372781065, 3599.31, 0.99, 9.29, 55.02],
 [0.55, 552.5452939131784, 0.42231075697211157, 2368.22, 0.99, 9.29, 54.96],
 [0.61, 543.8079308923195, 0.5130434782608696, 3080.53, 0.99, 9.29, 51.07],
 [0.66, 458.49674786705725, 0.5816326530612245, 3919.2, 0.99, 9.29, 58.77],
 [0.65, 501.72798368149245, 0.5761589403973509, 3703.35, 0.99, 9.29, 59.29],
 [0.69, 404.305126783455, 0.6666666666666666, 4653.74, 0.99, 9.29, 94.19],
 [0.71, 446.59081186545836, 0.7471264367816092, 5704.85, 0.99, 9.29, 86.18],
 [0.68, 494.87598903781685, 0.6312056737588653, 4173.83, 0.99, 9.29, 76.72],
 [0.67, 529.3304824724493, 0.6180904522613065, 4054.95, 0.99, 9.29, 54.85],
 [0.69, 471.8498871295094, 0.6160714285714286, 4510.52, 1.0, 9.29, 60.26],
 [0.67, 484.4187086458591, 0.6141732283464567, 4044.89, 0.99, 9.29, 58.72],
 [0.57, 504.3425116919247, 0.4645161290322581, 2613.11, 0.99, 9.29, 62.84],
 [0.65, 520.9486152841421, 0.5737704918032787, 3545.04, 0.99, 9.29, 46.8],
 [0.61, 492.7253685157205, 0.5144927536231884, 3087.59, 0.99, 9.29, 80.64],
 [0.66, 455.3876891600541, 0.6736842105263158, 4744.6, 0.99, 9.29, 83.21],
 [0.61, 485.9812404361672, 0.5116279069767442, 3100.78, 0.99, 9.29, 74.38],
 [0.67, 506.2595033026967, 0.6075949367088608, 4037.01, 0.99, 9.29, 75.68],
 [0.59, 541.164605185504, 0.49107142857142855, 2833.63, 0.99, 9.29, 59.09],
 [0.62, 537.0638028127662, 0.5581395348837209, 3467.82, 0.99, 9.29, 44.54],
 [0.59, 528.8267030694535, 0.5050505050505051, 3044.59, 0.99, 9.29, 44.46],
 [0.65, 508.75963352323834, 0.5493827160493827, 3465.94, 0.99, 9.29, 68.19],
 [0.59, 473.61984483944957, 0.5350877192982456, 3165.59, 0.98, 9.29, 68.36],
 [0.63, 503.695260241363, 0.525974025974026, 3233.26, 0.99, 9.29, 65.4],
 [0.64, 533.2718793265369, 0.5603864734299517, 3606.62, 0.99, 9.29, 43.19],
 [0.64, 526.2690188904886, 0.5751295336787565, 3695.67, 0.99, 9.29, 59.25],
 [0.7, 489.7839799950911, 0.582089552238806, 4008.69, 0.99, 9.29, 82.75],
 [0.65, 507.51738152338265, 0.6125, 4002.34, 0.99, 9.29, 64.22],
 [0.68, 458.49674786705725, 0.6326530612244898, 4525.2, 0.99, 9.29, 88.12],
 [0.72, 418.9654742026425, 0.7121212121212122, 5224.98, 0.99, 9.29, 65.55],
 [0.5, 517.0483995038152, 0.4943181818181818, 2805.4, 0.98, 8.65, 68.8],
 [0.67, 465.3960350157523, 0.6857142857142857, 4825.4, 0.99, 8.65, 72.9],
 [0.61, 501.0635294096256, 0.5466666666666666, 3337.78, 0.99, 8.65, 79.94],
 [0.71, 445.4347296253507, 0.6511627906976745, 4483.5, 0.99, 8.65, 84.98],
 [0.6, 494.1642422609304, 0.5428571428571428, 3251.02, 0.99, 8.65, 63.91],
 [0.59, 529.3304824724493, 0.46733668341708545, 2823.16, 0.99, 8.65, 60.37],
 [0.57, 558.724865840025, 0.4606741573033708, 2572.35, 0.99, 8.65, 42.85],
 [0.59, 573.3341276897746, 0.47249190938511326, 2724.31, 0.99, 8.65, 42.96],
 [0.55, 556.4520407322693, 0.48659003831417624, 2710.18, 0.99, 8.65, 32.86],
 [0.54, 534.7107530717468, 0.3952380952380952, 2159.18, 0.99, 8.65, 47.74],
 [0.64, 538.4495062789089, 0.555045871559633, 3471.09, 0.99, 8.65, 44.61],
 [0.55, 515.3291594497779, 0.44508670520231214, 2449.8, 0.98, 8.65, 51.86],
 [0.66, 522.5746673713202, 0.5483870967741935, 3594.06, 0.99, 8.65, 53.32],
 [0.6, 541.164605185504, 0.48214285714285715, 2799.35, 0.99, 8.65, 50.4],
 [0.54, 556.4520407322693, 0.40229885057471265, 2176.71, 0.99, 8.65, 44.85],
 [0.48, 534.7107530717468, 0.43333333333333335, 2330.61, 0.98, 6.73, 53.38],
 [0.54, 554.907608489522, 0.490272373540856, 2790.96, 0.99, 8.8, 53.68],
 [0.57, 537.9897353540459, 0.4930875576036866, 2899.62, 0.99, 8.8, 73.7],
 [0.58, 564.8974238161206, 0.528169014084507, 3037.84, 0.99, 8.8, 45.45],
 [0.6, 537.9897353540459, 0.47465437788018433, 2751.81, 0.99, 8.8, 51.48],
 [0.62, 553.7334267018537, 0.5078740157480315, 3041.11, 0.99, 8.8, 51.82],
 [0.6, 522.5746673713202, 0.510752688172043, 3047.75, 0.99, 8.8, 53.78],
 [0.53, 560.947179518496, 0.3992673992673993, 2198.34, 0.99, 8.8, 59.82],
 [0.62, 545.9585514144159, 0.5404255319148936, 3260.12, 0.99, 8.8, 37.9],
 [0.61, 544.673737166631, 0.5344827586206896, 3154.73, 0.99, 8.8, 34.14],
 [0.59, 563.4789603169249, 0.48214285714285715, 2776.53, 0.99, 8.8, 34.6],
 [0.6, 561.312810638807, 0.5437956204379562, 3231.13, 0.99, 8.8, 57.06],
 [0.58, 566.6426688112432, 0.4844290657439446, 2793.07, 0.99, 8.8, 29.96],
 [0.5, 546.383180502561, 0.3940677966101695, 2021.69, 0.98, 8.8, 43.79],
 [0.53, 533.2718793265369, 0.5024154589371981, 2906.49, 0.98, 8.53, 61.99],
 [0.62, 538.9071729816501, 0.547945205479452, 3335.63, 0.99, 8.53, 66.4],
 [0.67, 519.8497031265827, 0.580110497237569, 3745.31, 0.99, 8.53, 59.93],
 [0.67, 518.7385805840755, 0.6089385474860335, 3951.19, 0.99, 8.53, 63.89],
 [0.65, 535.6586274672012, 0.5471698113207547, 3464.31, 0.99, 8.53, 66.8],
 [0.65, 536.5976015021852, 0.5373831775700935, 3395.49, 0.99, 8.53, 35.68],
 [0.66, 549.7168225293202, 0.5737704918032787, 3596.14, 0.99, 8.53, 44.42],
 [0.61, 540.2677381872279, 0.5405405405405406, 3257.45, 0.99, 8.53, 28.82],
 [0.55, 542.4950017481403, 0.5154185022026432, 2996.37, 0.98, 8.26, 57.08],
 [0.64, 515.9055299214529, 0.5804597701149425, 3607.48, 0.99, 8.26, 73.94],
 [0.59, 531.8119993844216, 0.47549019607843135, 2805.17, 0.99, 8.26, 74.57],
 [0.62, 524.1747015059642, 0.5502645502645502, 3308.98, 0.99, 8.26, 72.61],
 [0.64, 530.3304908059076, 0.6019900497512438, 3820.7, 0.99, 8.26, 62.27],
 [0.66, 509.9866427824199, 0.573170731707317, 3701.67, 0.99, 8.26, 54.52],
 [0.64, 496.98132995760005, 0.5902777777777778, 3735.53, 0.99, 8.26, 72.96],
 [0.55, 547.2270673671475, 0.5504201680672269, 3289.67, 0.98, 9.78, 53.29],
 [0.64, 519.295685089021, 0.5722222222222222, 3561.11, 0.99, 9.78, 66.84],
 [0.67, 526.7858159063328, 0.5979381443298969, 3833.56, 0.99, 9.78, 54.57],
 [0.65, 547.2270673671475, 0.6008403361344538, 3827.77, 0.99, 9.78, 39.78],
 [0.65, 531.3205979041787, 0.5763546798029556, 3673.95, 0.99, 9.78, 34.12],
 [0.58, 578.6897381366708, 0.6656441717791411, 4586.55, 1.0, 9.78, 28.94],
 [0.66, 536.5976015021852, 0.5981308411214953, 3850.99, 0.99, 9.78, 17.89],
 [0.65, 583.4810737062605, 0.6081871345029239, 3881.54, 0.99, 9.78, 24.44],
 [0.64, 548.8937726156687, 0.6033057851239669, 3862.44, 0.99, 9.78, 48.38],
 [0.62, 537.0638028127662, 0.5674418604651162, 3447.05, 0.99, 9.78, 49.65],
 [0.66, 558.724865840025, 0.6254681647940075, 4172.59, 0.99, 9.78, 31.76],
 [0.77, 460.51701859880916, 0.76, 5900.0, 1.0, 9.78, 52.02],
 [0.74, 380.66624897703196, 0.8444444444444444, 7032.1, 0.99, 9.78, 6.75],
 [0.65, 556.0681631015527, 0.6807692307692308, 4789.35, 1.0, 9.78, 33.7],
 [0.65, 561.6771097666572, 0.6545454545454545, 4497.72, 0.99, 9.78, 29.72],
 [0.63, 560.947179518496, 0.5604395604395604, 3473.28, 0.99, 9.78, 16.74],
 [0.7, 540.2677381872279, 0.6531531531531531, 4480.97, 0.99, 9.78, 22.34],
 [0.62, 537.0638028127662, 0.5441860465116279, 3204.76, 0.99, 9.78, 20.53],
 [0.66, 534.7107530717468, 0.6047619047619047, 3877.1, 0.99, 9.78, 33.24],
 [0.62, 581.4130531825066, 0.5283582089552239, 3165.78, 0.99, 9.78, 16.26],
 [0.66, 541.164605185504, 0.6026785714285714, 3860.01, 0.99, 9.78, 27.36],
 [0.7, 552.5452939131784, 0.6374501992031872, 4250.09, 0.99, 9.78, 16.54],
 [0.65, 566.9880922980519, 0.5896551724137931, 3701.31, 0.99, 9.78, 21.33],
 [0.63, 562.0400865717149, 0.5579710144927537, 3419.19, 0.99, 9.78, 36.59],
 [0.64, 553.7334267018537, 0.5866141732283464, 3712.26, 0.99, 9.78, 38.83],
 [0.61, 531.3205979041787, 0.541871921182266, 3298.79, 0.99, 9.78, 39.53],
 [0.65, 541.610040220442, 0.5911111111111111, 3799.31, 0.99, 9.78, 29.84],
 [0.64, 554.5177444479563, 0.5859375, 3722.84, 0.99, 9.78, 24.87],
 [0.66, 515.3291594497779, 0.5838150289017341, 3794.98, 0.99, 9.78, 44.53],
 [0.69, 567.3323267171493, 0.6323024054982818, 4342.41, 1.0, 9.78, 27.0],
 [0.63, 554.5177444479563, 0.578125, 3636.47, 0.99, 9.78, 21.9],
 [0.64, 556.0681631015527, 0.55, 3396.45, 0.99, 9.78, 23.61],
 [0.51, 540.2677381872279, 0.42792792792792794, 2364.26, 0.98, 7.78, 68.45],
 [0.64, 484.4187086458591, 0.6141732283464567, 4003.97, 0.99, 7.78, 64.05],
 [0.59, 518.1783550292085, 0.5056179775280899, 3076.0, 0.99, 7.78, 57.59],
 [0.52, 576.8320995793772, 0.390625, 2032.42, 0.99, 7.78, 37.94],
 [0.48, 567.6753802268282, 0.4006849315068493, 2024.07, 0.99, 7.86, 55.51],
 [0.61, 557.9729825986223, 0.5547169811320755, 3389.96, 0.99, 7.86, 48.09],
 [0.65, 537.0638028127662, 0.6232558139534884, 4087.4, 0.99, 7.86, 51.23],
 [0.52, 563.8354669333745, 0.4626334519572954, 2622.31, 0.99, 8.02, 57.59],
 [0.68, 487.5197323201151, 0.6106870229007634, 4264.32, 0.99, 8.02, 75.36],
 [0.63, 482.0281565605037, 0.5, 3128.25, 0.99, 8.02, 73.49],
 [0.63, 524.7024072160486, 0.5263157894736842, 3279.78, 0.99, 8.02, 64.66],
 [0.6, 511.7993812416755, 0.49101796407185627, 3305.25, 0.99, 8.02, 73.88],
 [0.59, 494.1642422609304, 0.45714285714285713, 2856.12, 0.99, 8.02, 71.16],
 [0.63, 509.3750200806762, 0.5705521472392638, 3623.02, 0.99, 8.02, 56.38],
 [0.56, 546.8060141135131, 0.45569620253164556, 2522.74, 0.99, 8.02, 58.91],
 [0.49, 556.4520407322693, 0.41379310344827586, 2111.83, 0.98, 8.57, 64.95],
 [0.55, 529.3304824724493, 0.45226130653266333, 2480.75, 0.99, 8.57, 46.35],
 [0.59, 558.3496308781699, 0.47368421052631576, 2735.6, 0.99, 8.57, 59.93]]

In [13]:
df = pd.DataFrame(result, columns = ['TTratio_WD', 'HonoreMeasureR_WD', 'hapax_WD', 'YuleK_WD', 'SimpsonIndex_WD', 'Shannon_WD', 'FR_readerablity'])
df

TTratio_WD  HonoreMeasureR_WD  hapax_WD  YuleK_WD  SimpsonIndex_WD  \
0          0.57         563.121178  0.562724   3386.13             0.99   
1          0.63         599.893656  0.555831   3341.32             0.99   
2          0.58         585.220248  0.508621   2878.19             0.99   
3          0.62         572.031178  0.508197   3014.46             0.99   
4          0.57         608.677473  0.525000   2946.59             0.99   
..          ...                ...       ...       ...              ...   
995        0.63         509.375020  0.570552   3623.02             0.99   
996        0.56         546.806014  0.455696   2522.74             0.99   
997        0.49         556.452041  0.413793   2111.83             0.98   
998        0.55         529.330482  0.452261   2480.75             0.99   
999        0.59         558.349631  0.473684   2735.60             0.99   

     Shannon_WD  FR_readerablity  
0          8.69            42.06  
1          8.69            25.07  
2          8.69            40.24  
3          8.69            38.30  
4          8.69            25.08  
..          ...              ...  
995        8.02            56.38  
996        8.02            58.91  
997        8.57            64.95  
998        8.57            46.35  
999        8.57            59.93  

[1000 rows x 7 columns]

In [14]:
#컬럼 합산 평균값 계산하기
TTratio_WD_mean = [df['TTratio_WD'].mean()] * 100
TTratio_WD_mean

[0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261,
 0.59261]

In [26]:
HonoreMeasureR_WD_mean = df['HonoreMeasureR_WD'].mean()
HonoreMeasureR_WD_mean

539.9944937764656

In [27]:
hapax_WD_mean = df['hapax_WD'].mean() * 1000
hapax_WD_mean

513.3095112466135

In [28]:
YuleK_WD_mean = df['YuleK_WD'].mean() * 0.1
HonoreMeasureR_WD_mean
YuleK_WD_mean

308.23864100000003

In [31]:
HonoreMeasureR_WD_mean

539.9944937764656

In [33]:
SimpsonIndex_WD_mean = df['SimpsonIndex_WD'].mean() * 100
SimpsonIndex_WD_mean

98.915

In [36]:
Shannon_WD_mean = df['Shannon_WD'].mean() * 100
Shannon_WD_mean

865.779

In [37]:
# 가독성
FR_readerablity_mean = df['FR_readerablity'].mean()
FR_readerablity_mean

50.71931

In [38]:
# Writing Diversity ratio
wri_div_mean = (TTratio_WD_mean + HonoreMeasureR_WD_mean + 
                hapax_WD_mean + YuleK_WD_mean + HonoreMeasureR_WD_mean + 
                SimpsonIndex_WD_mean + Shannon_WD_mean)/6 

wri_div_mean

array([477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8039583,
       477.8039583, 477.8039583, 477.8039583, 477.8039583, 477.8

In [23]:
one_ps_char_desc = wri_div_mean  # 이하 -13 ~ +17 이상 범위로 Lacking , Ideal, Overboard 
ideal_mean = 50 # 1000명의 평균값 (writing diversity)


min_ = int(ideal_mean-ideal_mean*0.6)
print('min_', min_)
max_ = int(ideal_mean+ideal_mean*0.6)
print('max_: ', max_)
div_ = int(((ideal_mean+ideal_mean*0.6)-(ideal_mean-ideal_mean*0.6))/3)
print('div_:', div_)


min_ 20
max_:  80
div_: 20


In [24]:
cal_abs = abs(ideal_mean - one_ps_char_desc) # 개인 - 단체 값의 절대값계산

print('cal_abs 절대값 :', cal_abs)
compare = (one_ps_char_desc + ideal_mean)/7
print('compare :', compare)

if one_ps_char_desc > ideal_mean: # 개인점수가 평균보다 클 경우는 overboard
    if cal_abs > compare: # 개인점수가 개인평균차의 절대값보다 클 경우, 즉 차이가 많이 날경우
        print("Overboard")
    else: #차이가 많이 안나면
        print("Ideal")
        
    
elif one_ps_char_desc < ideal_mean: # 개인점수가 평균보다 작을 경우 lacking
    if cal_abs > compare: #차이가 많이나면 # 개인점수가  평균보다 작을 경우 Lacking이고 
        print("Lacking")
    else: #차이가 많이 안나면
        print ("Ideal")
        
else:
    print("Ideal")


cal_abs 절대값 : [3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057 3.74846057
 3.74846057 3.74846057 3.74846057 3.74846057 3.7

ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()